In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import warnings
import openpyxl
import re
import os
from variableUtils import *
from Utils import *
from ClassUtils import *
from pprint import pprint
import json
from collections import defaultdict
from sklearn.ensemble import RandomForestRegressor
from sklearn.impute import SimpleImputer
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import matplotlib.pyplot as plt
from matplotlib.patches import Rectangle
from reportlab.lib.pagesizes import letter, landscape, A4, A3
from reportlab.platypus import SimpleDocTemplate, Table, TableStyle, PageBreak, Paragraph, Spacer, Image
from reportlab.lib import colors
from matplotlib.backends.backend_pdf import PdfPages
from reportlab.platypus import Paragraph, Spacer, KeepTogether, KeepInFrame
from reportlab.lib.styles import getSampleStyleSheet, ParagraphStyle
from reportlab.lib.units import inch
import io
from openpyxl import load_workbook
from openpyxl.styles import PatternFill
from openpyxl.formatting.rule import FormulaRule
import PIL
import ast
from adjustText import adjust_text
warnings.filterwarnings('ignore')
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
print(sns.__version__)


In [ ]:
# Load the ebelWeights and ebelMatrix from the saved Excel files
ebelWeightsSavePath = os.path.join('2025', 'ebelWeights.xlsx')
ebelMatrixSavePath = os.path.join('2025', 'ebelMatrix.xlsx')
ebelWeights = pd.read_excel(ebelWeightsSavePath, sheet_name=None)
ebelMatrix = pd.read_excel(ebelMatrixSavePath, sheet_name=None)
importanceWeights = {"Essential": 5, "Important": 3, "Non-essential": 1}
def getWeight(row, ebelDf):
    importance = row['Importance']
    difficulty = row['Difficulty']
    return ebelDf.loc[importance, difficulty]


for key, df in ebelWeights.items():

    df.set_index('MarkingChecklist', inplace=True)
    if 'scoreWeight' not in df.columns:
        df['scoreWeight'] = df['Importance'].map(importanceWeights)

    # ebel cutoffs
    if key not in ebelMatrix.keys():
        print(f"Key {key} not found in ebelMatrix")
        continue
    ebelDf = ebelMatrix[key].set_index('Importance')
    df['ebelWeight'] = df.apply(getWeight, axis=1, ebelDf=ebelMatrix[key].set_index('Importance'))
    ebelSum = df['ebelWeight'].sum()
    ebelCutoff = ebelSum /len(df)
    ebelWeightedSum = df['ebelWeight'] * df['scoreWeight']
    ebelWeightedSum = ebelWeightedSum.sum()
    ebelWeightedCutoff = ebelWeightedSum / df['scoreWeight'].sum()
    # if key!= '524':
        # continue
    print(f"========================\nKey: {key}")
    # display(df.head())
    print(f"EBEL Cutoff: {round(ebelCutoff,2)}")
    # print(f"EBEL Weighted Sum: {ebelWeightedSum.sum()}| {df['scoreWeight'].sum()}")
    print(f"EBEL Weighted Cutoff: {round(ebelWeightedCutoff,2)}")

### Json to excel sheet

In [ ]:
# jsonfilepath = '2025\BOH2\Form 1\\boh2.json'
# jsonfilepath = '2025\DDS2\\dds2.json'
# jsonfilepath = '2025\DDS1\data.json'
# jsonfilepath = '2025\\all_data.json'
jsonfilepath = '2025\\BOH1\\boh1.json'
# jsonfilepath = '2025\mini CEX\data.json'
# jsonfilepath = '2025/mini CEX/boh1.json'
folder, file, ext = getFolderandFileName(jsonfilepath)
with open(jsonfilepath, encoding='utf-8') as f:
    data = json.load(f)
# display(data)
print(json.dumps(data, indent=4))

In [ ]:
# Fields to pull out from supervisor_data
supervisorMainFields = ['time_mgmt', 'entrustment', 'communication', 'professionalism', 'assessor_feedback', 
                        'clinical_incident', 'patient_complexity']
# Field to pull out from student_data
studentMainFields = ['student_feedback']
def getStudentList(listpath, cohort='BOH3'):
    listdf = pd.read_excel(listpath, keep_default_na=False, na_values=[''])
    if cohort is not None:
        listdf = listdf[listdf['Cohort'] == cohort]
    validIds = listdf['Student ID'].to_list()
    # convert to int
    validIds = [int(id) for id in validIds]
    print(f"Number of valid student IDs in {cohort}: {len(validIds)}")
    return validIds
validIds = getStudentList('2025\RE_ Student List.xlsx', cohort=None)

def jsonToExcel(data, supervisorMainFields, studentMainFields, folder, outputFile):
    flattenedEntries = []
    nestedEntries = []
    dataDict_flat = {}
    for entry in data["result"]:
        date = entry.get("date")
        # print("Student Id:", entry.get('student_number'))
        if entry.get('student_number') not in validIds:
            print(f"Skipping entry with student_id {entry.get('student_number')} {entry.get('student_name')} as it is not in the valid IDs list.")
            continue
        # Base fields
        baseData = {k: v for k, v in entry.items() if not isinstance(v, dict)}
        
        # Supervisor fields
        supervisorData = entry.get('supervisor_data', {})
        supervisorFieldsExtracted = {k: supervisorData.get(k) for k in supervisorMainFields}
        supervisorRemainingData = {k: v for k, v in supervisorData.items() if k not in supervisorMainFields}
        
        # Student fields
        studentData = entry.get('student_data', {})
        studentFieldsExtracted = {k: studentData.get(k) for k in studentMainFields}
        studentRemainingData = {k: v for k, v in studentData.items() if k not in studentMainFields}
        
        # Fully flattened (all keys)
        flattenedEntry = {**baseData, **studentData, **supervisorData}
        if date not in dataDict_flat:
            dataDict_flat[date] = []
        dataDict_flat[date].append(flattenedEntry)
        flattenedEntries.append(flattenedEntry)

        # Nested version
        nestedEntry = {
            **baseData,
            **supervisorFieldsExtracted,
            **studentFieldsExtracted,
            'student_data': json.dumps(studentRemainingData, indent=2, ensure_ascii=False),
            'supervisor_data': json.dumps(supervisorRemainingData, indent=2, ensure_ascii=False)
        }
        nestedEntries.append(nestedEntry)

    with pd.ExcelWriter(outputFile, engine='openpyxl') as writer:
        # Save flattened data
        for date, records in dataDict_flat.items():
            safeSheetName = str(date).replace('/', '-').replace('\\', '-').replace('*', '').replace('[', '').replace(']', '')[:31]
            df = pd.DataFrame(records)
            df.to_excel(writer, sheet_name=f'{safeSheetName}', index=False)

        # Save flattened all_data
        df_all_flat = pd.DataFrame(flattenedEntries)
        df_all_flat.to_excel(writer, sheet_name='all_data_flat', index=False)

        # Save nested all_data
        df_all_nested = pd.DataFrame(nestedEntries)
        df_all_nested.to_excel(writer, sheet_name='all_data_nested', index=False)

jsonToExcel(data, supervisorMainFields, studentMainFields, folder, os.path.join(folder, 'all_data_combined.xlsx'))


### Create student performance time series and other reports

In [ ]:
# workbookpath = '2025\BOH2\Form 1\\all_data_combined.xlsx'
workbookpath = '2025\BOH1\\all_data_combined.xlsx'
# workbookpath = '2025\mini CEX\\boh1 all_data_combined.xlsx'
# workbookpath = '2025\mini CEX\\all_data_combined.xlsx'
# workbookpath = '2025\DDS2\\all_data_combined.xlsx'
# workbookpath = '2025\DDS1\\all_data_combined.xlsx'
folder, file, ext = getFolderandFileName(workbookpath)
df = pd.read_excel(workbookpath, sheet_name='all_data_nested')
flatDf = pd.read_excel(workbookpath, sheet_name='all_data_flat')
# define variable names
colId = 'Student ID'
colName = 'Student Name'
colDate = 'Date'
colCI = 'CI'
colTS = 'TS'
colES = 'ES'
colCS = 'CS'
colPS = 'PS'
colAssessorName = 'Assessor Name'
colAssessorFeedback = 'Assessor Feedback'
colPatientComplexity = 'Patient Complexity'
mcCols = [col for col in df.columns if 'MC' in col]
assessormcCols = [col for col in mcCols if 'assessor' in col]
studentmcCols = [col for col in mcCols if 'student' in col]
# display(df.head())
# drop na Student ID
df.rename(columns={'student_number':colId, 'student_name': colName, 'date': colDate,
                   'time_mgmt': colTS, 'entrustment': colES, 'communication': colCS, 'professionalism': colPS, 
                   'clinical_incident': 'CI', 'patient_complexity': 'Patient Complexity', 'assessor_name': colAssessorName,
                   'assessor_feedback': colAssessorFeedback}, inplace=True)
df.dropna(subset=[colId], inplace=True)
df[colId] = df[colId].astype(int)
df[colTS] = df[colTS].astype('Int64')
df[colES] = df[colES].astype('Int64')
df[colCS] = df[colCS].astype('Int64')
df[colPS] = df[colPS].astype('Int64')

headingStyleLarge = ParagraphStyle('Heading1', parent=styles['Heading1'], fontSize=72, alignment=1)  # Centered

df[colPatientComplexity] = df[colPatientComplexity].fillna('')
df[colPatientComplexity] = df[colPatientComplexity].astype(str)
df[colCI] = df[colCI].fillna('')
commonList = [
    'assessment_id', colName, colId, colAssessorName, colDate,
    'cohort', 'subject', 'type', 'student_submitted', 'assessor_submitted',
    colTS, colES, colCS, colPS,
    colAssessorFeedback, colCI, colPatientComplexity, 'student_feedback'
]
beforeCols = ['assessment_id', colName, colId,  colDate, colAssessorName, 'cohort', 'subject', 'type', colPatientComplexity]
rubricCols = [colTS, colES, colCS, colPS]
feedbackCols = [colCI, colAssessorFeedback, 'student_feedback']   

replaceNotReviwedwithNo = False
display(df.head())

# get weights of marking checklist and rubrics
weightPS = 0.05
weightTS = 0.025
weightES = 0.15
weightCS = 0.0
weightMC = round(1 - weightPS - weightTS - weightES - weightCS, 3)
print(f"Weight of PS: {weightPS}, TS: {weightTS}, ES: {weightES}, CS: {weightCS}, MC: {weightMC}")


In [ ]:
def extractCodes(supervisorDataStr):
    try:
        data = json.loads(supervisorDataStr)
        codes = set()
        for key in data.keys():
            if 'MC' in key  and 'positioning' not in key and 'Consent' not in key and 'Record' not in key and 'infection' not in key:
                code = key.split('_')[1]
                codes.add(code)
        return sorted(codes)
    except Exception:
        return []
    
# Expand the JSON with scores having two levels of keys
def expandJson(row):
    jsonDict = json.loads(row)
    flatDict = {}
    for outerKey, innerDict in jsonDict.items():
        for innerKey, value in innerDict.items():
            flatDict[f'{outerKey}_{innerKey}'] = value
    return pd.Series(flatDict)

# get row wise scores for each item code
def getRowWiseScores(df):
    # check if supervisor_data is a string and convert to json
    # if isinstance(df['supervisor_data'].iloc[0], str):
    #     # print("Converting supervisor_data to JSON")
    #     # convert to json
    #     df['supervisor_data'] = df['supervisor_data'].apply(lambda x: json.loads(x))
        # convert to json
    df['supervisor_data'] = df['supervisor_data'].apply(lambda x: json.loads(x))
    scoresList = []

    for idx, row in df.iterrows():    
        print(f"Row: {idx}")
        jsonData = pd.json_normalize(row['supervisor_data'])
        if replaceNotReviwedwithNo:
            jsonData.replace({'Not Reviewed': 'No'}, inplace=True)
        jsonData.replace({'Not Reviewed': 'NA', 'Not Assessed': 'NA'}, inplace=True)
        itemList = row['Item Codes']
        scoreDict = {}
        # print(f'Item Codes: {itemList}')
        for item in itemList:
            # print(f'Item Code: {item}')
            scoreDict[item] = {}
            mcCols = [key for key in row['supervisor_data'].keys() if f'{item}_MC' in key]
            itemDf = jsonData[mcCols]
            # display(itemDf.head())
            itemDf.columns = [col.split('_')[2] for col in itemDf.columns]
            # display(itemDf.head())
            # rename hte columns to MC\d+ extract
            itemYes = int(itemDf[itemDf == 'Yes'].count(axis=1).sum())
            itemNo = int(itemDf[itemDf == 'No'].count(axis=1).sum())
            itemNA = int(itemDf[itemDf == 'NA'].count(axis=1).sum())
            scoreDict[item]['Yes'] = itemYes
            scoreDict[item]['No']   = itemNo
            scoreDict[item]['NA'] = itemNA
            if itemYes + itemNo > 0:
                scoreDict[item]['% Yes'] = round((itemYes / (itemYes + itemNo) * 100), 2)
            else:
                scoreDict[item]['% Yes'] = np.nan

            # get the ebel cutoffs for the item code
            if item in ebelWeights.keys():
                weightDf = ebelWeights[item]
                # use only MC items that  are not NA
                notNA = itemDf[itemDf != 'NA']
                notNA = notNA.dropna(axis=1, how='all')
                if notNA.empty:
                    print(f'Item Code: {item} has no data')
                    continue
                # display(notNA.head())
                cutoff = 0
                weightedCutoff = 0
                weightedSum = 0
                denominator = 0
                # display(weightDf)
                for col in notNA.columns:
                    # print(cutoff, weightedCutoff, weightedSum, denominator)
                    try:
                        cutoff += weightDf.loc[col, 'ebelWeight']
                        weightedCutoff += weightDf.loc[col, 'ebelWeight'] * weightDf.loc[col, 'scoreWeight']
                        if notNA.loc[0, col] == 'Yes':
                            weightedSum += weightDf.loc[col, 'scoreWeight']
                        denominator += weightDf.loc[col, 'scoreWeight']
                    except KeyError:
                        print(f"KeyError: {col} not found in weightDf")
                        continue
                # print(f'Cutoff: {cutoff}, Weighted Cutoff: {weightedCutoff}, Weighted Sum: {weightedSum}, Denominator: {denominator}')
                cutoff = cutoff / len(notNA.columns)
                weightedCutoff = weightedCutoff / denominator
                weightedScore = round((weightedSum / denominator * 100), 2)

                totalScore = weightMC * weightedScore + (weightTS * row[colTS]/4 + weightES * row[colES]/4 + weightPS * row[colPS]/2 + weightCS * row[colCS]/2)*100
                # get dtype of each item in the above expression

                # print(f'Cutoff: {cutoff}, Weighted Cutoff: {weightedCutoff}, Weighted Sum: {weightedSum}, Denominator: {denominator}')
                try:
                    scoreDict[item] = scoreDict[item] | {'Cutoff': round(cutoff,2), 'Weighted Cutoff': round(weightedCutoff,2), 'Weighted Sum': int(weightedSum), 'Denominator': int(denominator),
                                                     'Weighted Score': weightedScore, 'Total Score': round(totalScore, 2)}
                except TypeError:
                    print(f"Error in item {item} with data: {scoreDict[item]}, student data: {row[colId]}")
                    print(cutoff, weightedCutoff, weightedSum, denominator, weightedScore, totalScore)
                    display(notNA.head())
        # pprint(scoreDict)        
        scoresList.append(json.dumps(scoreDict))
    df['Scores'] = scoresList
    df['supervisor_data'] = df['supervisor_data'].apply(lambda x: json.dumps(x, indent=2, ensure_ascii=False))

def getSeparatedItemDf(df):
    dfDict = {}
    # check if item codes is a string and convert to list
    df['Item Codes'] = df['Item Codes'].apply(lambda x: ast.literal_eval(x) if isinstance(x, str) else x)
    itemCodes = df['Item Codes'].sum()

    itemCodes = list(set(itemCodes))
    for item in itemCodes:
        # print(f'Item Code: {item}')
        # itemDf.set_index('assessment_id', inplace=True)
        itemDf = df[df['Item Codes'].apply(lambda x: item in x)] # select rows where item is in Item Codes
        if isinstance(itemDf['supervisor_data'].iloc[0], str):
            # print("Converting supervisor_data to JSON")
            # convert to json
            itemDf['supervisor_data'] = itemDf['supervisor_data'].apply(lambda x: json.loads(x))
        supervisorDataDf= itemDf['supervisor_data'].apply(pd.Series)
        if replaceNotReviwedwithNo:
            supervisorDataDf.replace({'Not Reviewed': 'No'}, inplace=True)
        supervisorDataDf.replace({'Not Reviewed': 'NA', 'Not Assessed': 'NA'}, inplace=True)
        # display(itemDf.head())
        # display(supervisorDataDf.head())
        # only take columns have item code in them
        # display(supervisorDataDf.head())
        validCols = [col for col in supervisorDataDf.columns if item in col]
        supervisorDataDf = supervisorDataDf[validCols]
        # rename columns to remove assessor_ text
        supervisorDataDf.columns = [col.split('assessor_')[-1] for col in supervisorDataDf.columns]

        # Step 1: Convert Yes/No to 1/0
        supervisordataDfBinary = supervisorDataDf.replace({'Yes': 1, 'No': 0, 'NA': np.nan})
        # display(supervisordataDfBinary.head())
        # Step 2: Calculate column scores
        columnScores = supervisordataDfBinary.sum(axis=0)

        # Step 3: Sort columns based on score (descending)
        sortedColumns = columnScores.sort_values(ascending=False).index

        # Step 4: Reorder dataframe columns
        sortedSupervisorDataDf = supervisorDataDf[sortedColumns]
        sortedSupervisorDataDf = sortedSupervisorDataDf.replace({'Yes': 1, 'No': 0})
        # display(sortedSupervisorDataDf.head())
        # display(supervisorDataDf.head())
        thiscommonList = [col for col in itemDf.columns if col in commonList]
        thisbeforeCols = [col for col in beforeCols if col in itemDf.columns]
        combinedDf= pd.concat([itemDf[thisbeforeCols], sortedSupervisorDataDf, itemDf[rubricCols], itemDf[feedbackCols]], axis=1)
        # display(combinedDf.head())
        expandedScores = itemDf['Scores'].apply(expandJson)
        validCols2 = [col for col in expandedScores.columns if item in col]
        expandedScores = expandedScores[validCols2]
        # display(expandedScores.head())
        combinedDf = pd.concat([combinedDf, expandedScores], axis=1)
        # display(combinedDf.head())
        dfDict[item] = combinedDf
    
    return dfDict

def plotStudentScoresTimeSeries(df, 
                      dateCol='Date', 
                      scoreDictCol='assessor_scores_dict', 
                      scoreKey='% Yes', 
                      fallbackKeys=None,
                      title='Student Performance Over Time'):
    """
    Creates and returns a scatter plot of scores over time with fallback keys.

    Args:
        df (pd.DataFrame): DataFrame with date and score dict columns.
        dateCol (str): Column name for date.
        scoreDictCol (str): Column with assessor score dictionaries.
        scoreKey (str): Primary key to extract.
        fallbackKeys (list of str): List of fallback keys to use if primary key missing.
        title (str): Title of the plot.

    Returns:
        matplotlib.figure.Figure: The generated figure object.
    """
    if fallbackKeys is None:
        fallbackKeys = []

    # df[dateCol] = pd.to_datetime(df[dateCol])

    expandedRows = []
    for _, row in df.iterrows():
        if not isinstance(row[scoreDictCol], dict):
            continue
        for itemCode, scoreDict in row[scoreDictCol].items():
            score = scoreDict.get(scoreKey)
            if score is None:
                for fbKey in fallbackKeys:
                    score = scoreDict.get(fbKey)
                    if score is not None:
                        break
            if score is not None:
                expandedRows.append({
                    'Date': row[dateCol],
                    'Item': itemCode,
                    'Score': score,
                    colAssessorName: row[colAssessorName],
                })

    expandedDf = pd.DataFrame(expandedRows)
    if expandedDf.empty:
        print(f"No valid data for '{scoreKey}' or fallbacks {fallbackKeys}.")
        return None

    # Plot
    fig, ax = plt.subplots(figsize=(11, 7))
    ax.scatter(expandedDf['Date'], expandedDf['Score'], color='blue')

    offestCounter = defaultdict(int)
    for _, row in expandedDf.iterrows():
        key = (row['Date'], row['Score'])
        offset = offestCounter[key] * 5
        offestCounter[key] += 1
        ax.annotate(f"{row['Item']}",# ({row[colAssessorName]})",
                    (row['Date'], row['Score']),
                    textcoords="offset points", xytext=(0, 5 + 2*offset),
                    ha='center', fontsize=6)
        # ax.annotate(f"{row['assessor_name']}",
        #             (row['Date'], row['Score']),
        #             textcoords="offset points", xytext=(0, -10 - 2*offset),
        #             ha='center', fontsize=6)

    ax.set_title(title)
    ax.set_xlabel("Date")
    ax.set_ylabel("Score (% Yes or Weighted)")
    ax.grid(True, linestyle='--', alpha=0.5)
    ax.tick_params(axis='x', rotation=45)
    ax.set_ylim(-5, 1.2*expandedDf['Score'].max())
    ax.set_yticks(range(0, int(expandedDf['Score'].max() + 1), int(max(expandedDf['Score'].max()//10, 1))))
    fig.tight_layout()

    return fig

def createTimeSeriesReport(df, scoreKey):
    elements = []
    df.sort_values(by=[colName], inplace=True)
    for id in df[colId].unique():
        studentDf = df[df[colId] == id]
        studentDf = studentDf[studentDf['assessor_submitted']]
        if studentDf.empty:
            continue
        name = studentDf[colName].values[0]
        studentDf[colDate] = pd.to_datetime(studentDf[colDate], format= 'mixed')
        studentDf.sort_values(by=colDate, inplace=True)
        studentDf[colDate] = studentDf[colDate].dt.strftime('%d/%m')
        # display(studentDf.head())
        
        # create 4 ubplots of time series of time mgmt, professionalism, communication, entrustment
        # Set variables
        xLabelRotation = 45
        forceIntegerYTicks = True

        fig, axs = plt.subplots(4, 1, figsize=(figSize[0], figSize[1]*0.7))  # 4 rows, 1 column
        # fig.suptitle(f'colId: {id}')
        if axs.ndim > 1:
            axs = axs.flatten()
        # Define plots
        plotConfigs = [
            (3, colTS, 'blue'),
            (1, colPS, 'green'),
            (2, colCS, 'orange'),
            (0, colES, 'red')
        ]
        try:
            for idx, label, color in plotConfigs:
                ax = axs[idx]
                ax.plot(studentDf[colDate], studentDf[label], label=label, color=color, marker='o')
                ax.set_title(label)
                ax.set_xlabel('Date')
                ax.set_ylim(0, studentDf[label].max() + 0.5)
                ax.tick_params(axis='x', rotation=xLabelRotation)
                ax.grid(True, linestyle='--', alpha=0.5)
                ax.set_yticks(range(0, int(studentDf[label].max()+1), 1))
                ax.set_yticklabels(range(0, int(studentDf[label].max()+1), 1))
                # if forceIntegerYTicks:
                #     ax.yaxis.get_major_locator().set_params(integer=True)

            plt.tight_layout(rect=[0, 0, 1, 0.95])
            imgrubric = addPlotImage(fig, 0.8)
        except Exception as e:
            print(f"Error in plotting: {e}")
            display(studentDf)
            imgrubric = None
        # create a table of the scores for each item code
        
        elements.append(Paragraph(f'{name} ({id})', subheadingStyle))
        elements.append(Spacer(1, 12))

        figScoreSeries = plotStudentScoresTimeSeries(studentDf, dateCol=colDate, scoreDictCol='Scores', title=f'Student ID: {id}', scoreKey=scoreKey, fallbackKeys=['% Yes'])
        if figScoreSeries is not None:
            imgMC = addPlotImage(figScoreSeries, 0.8)
            elements.append(imgMC)
            elements.append(Spacer(1, 12))

        elements.append(imgrubric)
        elements.append(PageBreak())
        # break

    return elements



In [ ]:
# item code df grouped by colId and date
def getItemCodeDf(df, colId, colName, colDate):
    itemCodeDf = df.groupby([colId, colDate])['Item Codes'].sum().reset_index()
    itemCodeDf[colName] = itemCodeDf[colId].apply(lambda x: df[df[colId] == x][colName].values[0])
    itemCodeDf = itemCodeDf[[colId, colName, colDate, 'Item Codes']]
    itemCodeDf.sort_values(by=[colName, colDate], inplace=True)
    # display(itemCodeDf.head())
    return itemCodeDf


# get unique number of dates for each student
def getUniqueDates(df, colId, colDate): 
    uniqueDatesDf = df.groupby([colId])[colDate].nunique().reset_index()
    uniqueDatesDf[colName] = uniqueDatesDf[colId].apply(lambda x: df[df[colId] == x][colName].values[0])
    uniqueDatesDf = uniqueDatesDf[[colId, colName, colDate]]
    uniqueDatesDf.rename(columns={colDate: 'Days attented'}, inplace=True)
    uniqueDatesDf.sort_values(by='Days attented', ascending=False, inplace=True)
    # display(uniqueDatesDf.head())
    return uniqueDatesDf

# entrustment level counts for each student
def getLevelCounts(df, colRubric = colES):
    levelCounts = (
        df
        .groupby([colId, colRubric])
        .size()
        .unstack(fill_value=0)  # Make levels into columns, missing levels = 0
    )
    # fill to have all level columns
    levelCounts = levelCounts.reindex(columns=[1, 2, 3, 4], fill_value=0)
    allLevelDict = {1: 'Lvl 1', 2: 'Lvl 2', 3: 'Lvl 3', 4: 'Lvl 4'}

    levelCounts.reset_index(inplace=True)
    levelCounts[colName] = levelCounts[colId].apply(lambda x: df[df[colId] == x][colName].values[0])
    levelCounts = levelCounts[[colId, colName] + list(allLevelDict.keys())]

    levelCounts.rename(columns= allLevelDict, inplace=True)
    levelCounts.sort_values(by=['Lvl 1', 'Lvl 2'], inplace=True, ascending=False)
    # remove columns with all 0 values
    levelCounts = levelCounts.loc[:, (levelCounts != 0).any(axis=0)]
    # display(levelCounts.head())

    overallEntrustmentCounts = df[colRubric].value_counts()
    overallEntrustmentCounts = overallEntrustmentCounts.reset_index()
    overallEntrustmentCounts.rename(columns={'index': colRubric, 0: 'Counts'}, inplace=True)
    return levelCounts, overallEntrustmentCounts

# get critical incident information
def getCriticalIncidents(df):
    # select rows where clinical_incident is not empty pd.na
    ciDf = df[df[colCI].notna()]
    ignoreList = ['Nil', 'None', 'No comments', 'No']
    ciDf = ciDf[~ciDf[colCI].str.strip().isin(ignoreList)]  
    ciDf = ciDf[ciDf[colCI].str.strip() != '']
    ciDf = ciDf[ciDf[colCI] != 'nan']
    # select only the columns we need
    ciDf = ciDf[[colId, colName, colDate, colCI]]
    display(ciDf.head())

    # group by colId to get counts
    ciCounts = ciDf.groupby([colId])[colCI].count().reset_index()
    ciCounts[colName] = ciCounts[colId].apply(lambda x: df[df[colId] == x][colName].values[0])
    ciCounts = ciCounts[[colId, colName, colCI]]
    ciCounts.rename(columns={colCI: 'CI Counts'}, inplace=True)
    ciCounts.sort_values(by='CI Counts', ascending=False, inplace=True)
    return ciDf, ciCounts


def getNPatients(df):
    # if patient complexity is not empty
    patientDf = df[df[colPatientComplexity].notna()]
    patientDf = patientDf[patientDf[colPatientComplexity].str.strip() != '']
    print('Patients', len(patientDf))
    # display(patientDf.head())
    # get counts of each student
    patientCounts = patientDf[colId].value_counts()
    patientCounts = patientCounts.reset_index()
    display(patientCounts.head())
    patientCounts.rename(columns={ 'count': 'Patient Counts'}, inplace=True)
    patientCounts[colName] = patientCounts[colId].apply(lambda x: df[df[colId] == x][colName].values[0])
    patientCounts = patientCounts[[colId, colName, 'Patient Counts']]
    patientCounts.sort_values(by='Patient Counts', ascending=False, inplace=True)
    display(patientCounts.head())
    return patientCounts

def createData(dfSim, title):
    elements = []
    elements.append(Spacer(1, 104*3))
    elements.append(Paragraph(title, headingStyleLarge))
    elements.append(Spacer(1, 12))
    itemCodeDfSim = getItemCodeDf(dfSim, colId, colName, colDate)
    
    # add table for entrustment level counts
    levelCountsSim, overallCountsSim  = getLevelCounts(dfSim)
    levelCountsTableSim= createTable(levelCountsSim, 'Entrustment Level Counts', colRatio=[1.3, 1.7, 1, 1, 1, 1], customTextCols=[1], bottomPadding=6, topPadding=6)
    elements.append(levelCountsTableSim)
    elements.append(Spacer(1, 32))
    
    # add table for professionalism, communication, time management level counts
    professionalismCountsSim, overallCountsSim = getLevelCounts(dfSim, colRubric=colPS)
    professionalismCountsTableSim = createTable(professionalismCountsSim, 'Professionalism Level Counts', colRatio=[1.3, 1.7, 1, 1, 1, 1], customTextCols=[1], bottomPadding=6, topPadding=6)
    elements.append(professionalismCountsTableSim)
    elements.append(Spacer(1, 32))

    communicationCountsSim, overallCountsSim = getLevelCounts(dfSim, colRubric=colCS)
    communicationCountsTableSim = createTable(communicationCountsSim, 'Communication Level Counts', colRatio=[1.3, 1.7, 1, 1, 1, 1], customTextCols=[1], bottomPadding=6, topPadding=6)
    elements.append(communicationCountsTableSim)
    elements.append(Spacer(1, 32))

    timeMgmtCountsSim, overallCountsSim = getLevelCounts(dfSim, colRubric=colTS)
    timeMgmtCountsTableSim = createTable(timeMgmtCountsSim, 'Time Management Level Counts', colRatio=[1.3, 1.7, 1, 1, 1, 1], customTextCols=[1], bottomPadding=6, topPadding=6)
    elements.append(timeMgmtCountsTableSim)
    elements.append(Spacer(1, 32))
    
    # add table for overall counts
    overallCountsTableSim = createTable(overallCountsSim, 'Overall Entrustment Level Counts', colRatio=[1.3, 1.7], bottomPadding=6, topPadding=6)
    elements.append(overallCountsTableSim)
    elements.append(PageBreak())

    # add table for critical incidents
    ciDfSim, ciCountsSim = getCriticalIncidents(dfSim)
    ciDfSim.rename(columns={colCI: 'Critical Incident'}, inplace=True)
    ciDfSimTable = createTable(ciDfSim, 'Critical Incidents', colRatio=[1, 1.3, 1, 5], customTextCols=[3, 1, 2], bottomPadding=6, topPadding=6, tableTextStyle=tableTextStyleSmall)
    elements.append(ciDfSimTable)
    elements.append(Spacer(1, 12))
    ciCountsSimTable = createTable(ciCountsSim, 'Critical Incident Counts', colRatio=[1, 1.3, 1.7], bottomPadding=6, topPadding=6)
    elements.append(ciCountsSimTable)
    elements.append(PageBreak())

    # add table for codes for each student
    for id in itemCodeDfSim[colId].unique():
        studentDf = itemCodeDfSim[itemCodeDfSim[colId] == id]
        studentName = studentDf[colName].values[0]
        studentDfExploded = studentDf.explode('Item Codes')
        studentDfItemCounts = studentDfExploded.groupby(['Item Codes']).size().reset_index(name='Counts').sort_values(by='Counts', ascending=False)
        studentDf['Item Codes'] = studentDf['Item Codes'].apply(lambda x: ', '.join(x))
        studentDf['Date formatted'] = pd.to_datetime(studentDf[colDate])
        studentDf.sort_values(by='Date formatted', inplace=True)
        thisTable = createTable(studentDf[['Date', 'Item Codes']], f'All Codes for {studentName} ({id})', colRatio=[1, 2], customTextCols=[1, 0], tableTextStyle=tableTextStyleSmall,
                                topPadding=8, bottomPadding=8)
        # elements.append(thisTable)
        # elements.append(Spacer(1, 12))
        # plot a bar graph of the counts
        if not studentDfItemCounts.empty:
            fig, ax = plt.subplots(figsize=(figSize[0]*1, figSize[1]*0.3))
            sns.barplot(x=studentDfItemCounts['Item Codes'], y=studentDfItemCounts['Counts'], ax=ax)
            ax.set_title(f'All Code Counts for {studentName} ({id})')
            ax.set_xlabel('Codes')
            ax.set_ylabel('Counts')
            ax.set_xticklabels(ax.get_xticklabels(), rotation=90)
            total = studentDfItemCounts['Counts'].sum()  # add a text box with the total number of codes
            ax.text(0.9, 0.9, f'Total: {total}', horizontalalignment='center', verticalalignment='center', transform=ax.transAxes)
            for j, v in enumerate(studentDfItemCounts['Counts']):   # show the counts on top of the bars
                ax.text(j, v + 0.2, str(v), color='black', ha='center', fontsize=8)
            ax.set_ylim(0, max(studentDfItemCounts['Counts'])*1.2)  # Set y-axis limit to accommodate text
            img = addPlotImage(fig, 0.75)
            elements.append(KeepTogether([thisTable, Spacer(1, 24), img]))
        # elements.append(Spacer(1, 12))

    # add table for unique dates
    uniqueDatesDfSim = getUniqueDates(dfSim, colId, colDate)
    # display(uniqueDatesDfSim.head())
    uniqueDatesDfSimTable = createTable(uniqueDatesDfSim, 'Dates Attented', colRatio=[1.3, 1.7, 1], customTextCols=[1, 0], bottomPadding=6, topPadding=6)
    elements.append(uniqueDatesDfSimTable)
    elements.append(PageBreak())
    return elements

# create table for scores
def createScoreTables(df):
    scoreElements = []
    totalDf= pd.DataFrame(columns=[colId, 'Student Name', 'Yes', 'No', 'NA'])
    for id in sorted(df[colId].unique()):
        studentDf = df[df[colId] == id]
        studentName = studentDf[colName].values[0]
        aggItems = {}

        for i, row in studentDf.iterrows():
            scoreDict = row['Scores']
            for item, values in scoreDict.items():
                if item not in aggItems:
                    aggItems[item] = {'Yes': 0, 'No': 0, 'NA': 0}
                aggItems[item]['Yes'] += int(values['Yes'])
                aggItems[item]['No'] += int(values['No'])
                aggItems[item]['NA'] += (values['NA'])
        # display(aggItems)
        try:
            studentScoreDf = pd.DataFrame.from_dict(aggItems, orient='index').reset_index().rename(columns={'index': 'Item Code'})
            # add row for total of each column
            studentScoreDf.loc['Total'] = studentScoreDf.sum(numeric_only=True)
            studentScoreDf.loc['Total', 'Item Code'] = 'Total'
            studentScoreDf['Yes'] = studentScoreDf['Yes'].astype(int)
            studentScoreDf['No'] = studentScoreDf['No'].astype(int)
            studentScoreDf['NA'] = studentScoreDf['NA'].astype(int)
            studentScoreDf['% Yes'] = ((studentScoreDf['Yes'] / (studentScoreDf['Yes'] + studentScoreDf['No'])) * 100).round(2)
            # add the values of the total row to totalDf
            totalYes = studentScoreDf.loc['Total', 'Yes']
            totalNo = studentScoreDf.loc['Total', 'No']
            totalNA = studentScoreDf.loc['Total', 'NA']
            totalDf = pd.concat([totalDf, pd.DataFrame({colId: [id], 'Student Name': [studentName], 'Yes': [totalYes], 'No': [totalNo], 'NA': [totalNA]})], ignore_index=True)
            # studentScoreDf['% Yes'] = studentScoreDf.apply(
            #     lambda x: (x['Yes'] / (x['Yes'] + x['No']) * 100) if (x['Yes'] + x['No']) != 0 else np.nan)
            # display(studentScoreDf.head())
            studentScoreTable = createTable(studentScoreDf, f'Scores for {studentName} ({id})', colRatio=[1, 1, 1, 1, 1], customTextCols=[], bottomPadding=6, topPadding=6)
            scoreElements.append(studentScoreTable)
            scoreElements.append(Spacer(1, 12))
        except Exception as e:
            print(f"Error in creating score table for {studentName} ({id}): {e}")
            display(studentDf.head())
            display(studentScoreDf.head())
        # studentDf['Scores'] = studentDf['Scores'].apply(lambda x: json.loads(x))
        # studentDfScores = pd.json_normalize(studentDf['Scores'])
    totalDf['% Yes'] = ((totalDf['Yes'] / (totalDf['Yes'] + totalDf['No'])) * 100).round(2)
    # totalDf.to_excel(f'{folder}\\BOH1 total scores.xlsx')
    return scoreElements, totalDf

In [ ]:
df_ = df.copy()
df_['Item Codes'] = df_['supervisor_data'].apply(extractCodes)
getRowWiseScores(df_)
df_.to_excel(f'{folder}\\all data scores.xlsx')

In [ ]:
dfDict = getSeparatedItemDf(df_)
# save the dfs to same workbook with different sheet names
filepath = f'{folder}\\allDataSeparatedbyItems.xlsx'
if os.path.exists(filepath):
    os.remove(filepath)
with pd.ExcelWriter(filepath, engine='openpyxl') as writer:
    for item, itemDf in dfDict.items():
        print(f'Saving {item} to {filepath}')   
        itemDf.to_excel(writer, sheet_name=item, index=False)
        print(f'Saved {item} to {filepath}')

### DDS2 patient analysis

In [ ]:
df['Item Codes'] = df['supervisor_data'].apply(extractCodes)
dfclinic = df[df['type']=='Clinic']
def getbarchart(df, colpie):
    pieData = df[colpie].value_counts()
    pieData = pieData.reset_index()
    # pieData.rename(columns={'index': colpie, colpie: 'Counts'}, inplace=True)
    # pieData['%'] = (pieData['Counts'] / pieData['Counts'].sum()) * 100
    total = pieData['count'].sum()
    display(pieData.head())

    fig, ax = plt.subplots(figsize=(figSize[0], figSize[1]*0.45))
    ax.bar(pieData[colpie], pieData['count'])
    # ax.set_xlabel(colpie)
    ax.set_ylabel("Count")
    ax.set_title(f"Distribution of {colpie}")
    for i, v in enumerate(pieData['count']):
        ax.text(i, v + 0.2, str(v), color='black', ha='center', fontsize=8)
    
    plt.xticks(rotation=45, fontsize=8)
    plt.tight_layout()

    return fig, pieData

figoverall,_ = getbarchart(dfclinic, 'patient_status')
img = addPlotImage(figoverall, 0.8)
colpatientstatus = 'patient_status'
doc = SimpleDocTemplate(f'{folder}\\DDS2 patient status report.pdf', pagesize=pageSize, rightMargin = rightMargin,
                        leftMargin = leftMargin, topMargin = topMargin, bottomMargin = bottomMargin)
elements = []
elements.append(KeepTogether([Paragraph('Patient Status Report overall', subheadingStyle), Spacer(1, 12), img]))
elements.append(Spacer(1, 36))
# get bar chart for each item code
allItems = dfclinic['Item Codes'].sum()
allItems = list(set(allItems))
for item in allItems:
    itemDf = dfclinic[dfclinic['Item Codes'].apply(lambda x: item in x)] # select rows where item is in Item Codes
    if itemDf.empty or len(itemDf) < 5:
        continue
    print(f'Item: {item}')
    display(itemDf.head())
    fig, pieData = getbarchart(itemDf, colpatientstatus)
    img = addPlotImage(fig, 0.8)
    # plt.show()
    title = Paragraph(f'Patient Status for {item}', subheadingStyle)
    elements.append(KeepTogether([title, Spacer(1, 12), img]))
    elements.append(Spacer(1, 36))

doc.build(elements)

# add a role column, I saw a patient maps to Operator, others map to Assistant
dfclinic['role'] = dfclinic[colpatientstatus].apply(lambda x: 'Operator' if 'I saw a patient' == x else 'Assistant')
# group by id
dfclinicgrouped = dfclinic.groupby([colId, 'role']).size().unstack(fill_value=0).reset_index()
dfclinicgrouped.columns.name = None  # Remove the index name
# dfclinicgrouped = dfclinicgrouped.rename_axis(None, axis=1)  # Remove the axis name
display(dfclinicgrouped.head())  
dfclinicgrouped['Student Name'] = dfclinicgrouped[colId].apply(lambda x: df[df[colId] == x][colName].values[0])
dfclinicgrouped = dfclinicgrouped[[colId, 'Student Name', 'Operator', 'Assistant']]
dfclinicgrouped.sort_values(by=['Operator', 'Assistant'], ascending=False, inplace=True)    
display(dfclinicgrouped.head())

dfclinicgrouped['% Operator'] = dfclinicgrouped['Operator'] / (dfclinicgrouped['Operator'] + dfclinicgrouped['Assistant']) * 100
dfclinicgrouped['% Operator'] = dfclinicgrouped['% Operator'].round(2)
display(dfclinicgrouped.head())

roletable = createTable(dfclinicgrouped, 'Student Role Counts', colRatio=[1.3, 1.7, 1, 1, 1], customTextCols=[1], bottomPadding=6, topPadding=6)
elements = []
elements.append(roletable)
doc2 = SimpleDocTemplate(f'{folder}\\DDS2 report by role.pdf', pagesize=pageSize, rightMargin = rightMargin,
                        leftMargin = leftMargin, topMargin = topMargin, bottomMargin = bottomMargin)
doc2.build(elements)

In [ ]:
def getWeeklyBarChart(df, colPie, dateCol='Date'):
    df[dateCol] = pd.to_datetime(df[dateCol], errors='coerce')
    df['Week'] = df[dateCol].dt.to_period('W').apply(lambda r: r.start_time)

    # Group and pivot
    weeklyCounts = df.groupby(['Week', colPie]).size().reset_index(name='count')
    pivotDf = weeklyCounts.pivot(index='Week', columns=colPie, values='count').fillna(0)
    pivotDf.index = pivotDf.index.strftime('%Y-%m-%d')
    newColumnOrder = ['I saw a patient', 'Failed to attend (FTA)', 'Patient cancelled within 24 hours','New patient block not filled',		'Unable to book a patient']
    pivotDf = pivotDf[newColumnOrder]
    display(pivotDf.head())
    fig, ax = plt.subplots(figsize=(figSize[0], figSize[1]))
    pivotDf.plot(kind='bar', stacked=True, ax=ax)

    ax.set_ylabel("Count")
    ax.set_title(f"Weekly Distribution of {colPie}")
    ax.legend(title=colPie)
    plt.xticks(rotation=45, ha='right')
    plt.tight_layout()

    return fig, pivotDf

figWeekly, _ = getWeeklyBarChart(dfclinic, 'patient_status', 'Date')
img = addPlotImage(figWeekly, 0.85)
elements = []
elements.append(KeepTogether([Paragraph('Weekly Patient Status Distribution', subheadingStyle), Spacer(1, 12), img]))

doc3 = SimpleDocTemplate(f'{folder}\\DDS2 weekly patient status report.pdf', pagesize=pageSize, rightMargin = rightMargin,
                        leftMargin = leftMargin, topMargin = topMargin, bottomMargin = bottomMargin)
doc3.build(elements)

### DDS2 examiner analysis

In [ ]:
# Examiner analysis:
import statsmodels.api as sm
from statsmodels.stats.multicomp import MultiComparison
import matplotlib.pyplot as plt
from scipy.stats import f_oneway, kruskal
from scipy.stats import pearsonr
from statsmodels.stats.multicomp import pairwise_tukeyhsd
workbookpath = '2025\DDS2\\all data scores.xlsx'
folder, file, ext = getFolderandFileName(workbookpath)
df = pd.read_excel(workbookpath)
assessorDf = pd.DataFrame(columns=['assessor_name', 'Date', 'Item', 'Yes', 'No', 'NA', '% Yes', 'Weighted Score', 'Entrustment'])
for i, row in df.iterrows():
    scoreDict = json.loads(row['Scores'])
    assessorName = row['assessor_name']
    for item, values in scoreDict.items():
        Yes = values['Yes']
        No = values['No']
        NA = values['NA']
    
        weightedScore = values.get('Weighted Score', np.nan)
        Yesper = values['% Yes']
        assessorDf = pd.concat([assessorDf, pd.DataFrame({'assessor_name': [assessorName], 'Item': [item],'Yes': [Yes], 'No': [No], 'Date': [row[colDate]],
                                                           'NA': [NA], '% Yes': [Yesper], 'Weighted Score': [weightedScore], 'Entrustment': row[colES]})], ignore_index=True) 

display(assessorDf.head())
# assessorDf.to_excel(f'{folder}\\assessorDf.xlsx', index=False)

In [ ]:
assessorDf= pd.read_excel(f'{folder}\\assessorDf.xlsx')
import matplotlib.cm as cm
from matplotlib.colors import to_hex
def assessorAnalysis(df, item=None, colScore ='Weighted Score'):
    display(df.head())
    # how many rows with not NA in the column
    print(f'Number of rows with not NA in the column {colScore}: {len(df[df[colScore].notna()])}')
    # change assessor names to dummy names assessor_1, assessor_2, etc.

    uniqueAssessors = df['assessor_name'].dropna().unique()
    palette = sns.color_palette("hls", n_colors=len(uniqueAssessors))
    cmap = cm.get_cmap('tab20', len(uniqueAssessors))   
    colors = [to_hex(cmap(i)) for i in range(len(uniqueAssessors))]
    groupedDf = df.groupby(['assessor_name']).agg({'Yes': 'sum', 'No': 'sum', 'NA': 'sum', colScore: 'mean'}).reset_index()
    # display(groupedDf.head())
    groupedDf['% Yes'] = ((groupedDf['Yes'] / (groupedDf['Yes'] + groupedDf['No'])) * 100).round(2)
    # display(groupedDf.head())

    # plot a bar graph of the counts
    groupedDf.sort_values(by=['% Yes'], ascending=False, inplace=True)
    fig, ax = plt.subplots(figsize=(figSize[0]*1.5, figSize[1]*0.3))
    sns.barplot(x=groupedDf['assessor_name'], y=groupedDf['% Yes'], ax=ax)
    ax.set_title(f'Assessor % Yes Counts for {item}' if item else 'Assessor % Yes Counts')
    ax.set_xlabel('Assessors')
    ax.set_ylabel('% Yes')
    ax.grid(True, linestyle='--', alpha=0.5)
    ax.set_xticklabels(ax.get_xticklabels(), rotation=90)
    for j, v in enumerate(groupedDf['% Yes']):   # show the counts on top of the bars
        ax.text(j, v + 2, str(v), color='black', ha='center', fontsize=8, rotation=90)
    ax.set_ylim(0, max(groupedDf['% Yes'])*1.2)  # Set y-axis limit to accommodate text
    plt.savefig(f'{folder}\\assessor analysis\\assessor_{item}_yes.png', dpi=300, bbox_inches='tight')

    # plot distribution of % Yes for each assessor
    plt.figure(figsize=(10, 6))
    sns.kdeplot(data=df, x=colScore, hue='assessor_name', linestyle='--', color=colors, fill=False)
    # a dotted kde for the overall distribution
    # sns.kdeplot(data=df, x=colScore, color='black', linestyle='-', label='Overall Distribution')
    plt.title(f"Distribution of Weighted Scores per Examiner {item}" if item else "Distribution of Weighted Scores per Examiner")
    plt.xlabel("Weighted Score")
    plt.tight_layout()
    plt.savefig(f'{folder}\\assessor analysis\\assessor_{item}_distribution.png', dpi=300, bbox_inches='tight')
    
    # box plot of weighted scores for each assessor
    mean_order = df.groupby('assessor_name')[colScore].mean().sort_values(ascending=False).index
    plt.figure(figsize=(10, 6))
    sns.boxplot(data=df, x='assessor_name', y=colScore, palette=colors, order=mean_order)
    plt.title(f"Box Plot of Weighted Scores per Examiner {item}" if item else "Box Plot of Weighted Scores per Examiner")
    plt.xlabel("Examiner")
    plt.ylabel("Weighted Score")
    plt.xticks(rotation=90)
    plt.tight_layout()
    plt.savefig(f'{folder}\\assessor analysis\\assessor_{item}_boxplot.png', dpi=300, bbox_inches='tight')

    # stats analysis
    grouped_scores = [group[colScore].dropna().values for name, group in df.groupby('assessor_name')]

    # Perform One-Way ANOVA
    anova_stat, anova_p = f_oneway(*grouped_scores)

    # Perform Kruskal-Wallis H-test (non-parametric alternative to ANOVA)
    kruskal_stat, kruskal_p = kruskal(*grouped_scores)

    # Summary of results
    statistical_summary = pd.DataFrame({
        'Test': ['One-Way ANOVA', 'Kruskal-Wallis H'],
        'Test Statistic': [anova_stat, kruskal_stat],
        'p-value': [anova_p, kruskal_p]
    })

    display(statistical_summary)

    # Post-hoc analysis if ANOVA is significant
    if anova_p < 0.05:
        mc = MultiComparison(df[colScore], df['assessor_name'])
        tukey_result = mc.tukeyhsd()
        tukey_summary = pd.DataFrame(data=tukey_result._results_table.data[1:], columns=tukey_result._results_table.data[0])
        display(tukey_summary[tukey_summary['reject'] == True])
        savefile = f'{folder}\\assessor analysis\\assessor_anova_results.xlsx' if item else f'{folder}\\assessor analysis\\anova_results.xlsx'
        if os.path.exists(savefile):    
            with pd.ExcelWriter(savefile, engine='openpyxl', mode='a', if_sheet_exists='replace') as writer:
                    tukey_summary[tukey_summary['reject'] == True].to_excel(writer, sheet_name=item if item else 'All', index=False)
        else:
            with pd.ExcelWriter(savefile, engine='openpyxl') as writer:
                tukey_summary[tukey_summary['reject'] == True].to_excel(writer, sheet_name=item if item else 'All', index=False)

namemap = {name: f'assessor_{i+1}' for i, name in enumerate(assessorDf['assessor_name'].unique())}
assessorDf['assessor_name'] = assessorDf['assessor_name'].replace(namemap)
# assessorAnalysis(assessorDf)
# now only for items 524
item = '524'
df2 = assessorDf[assessorDf['Item'] == item]
print(f'Number of rows for item {item}: {len(df2)}')
assessorAnalysis(df2, item, colScore='Weighted Score')
# now for 578
item = '578'
df2 = assessorDf[assessorDf['Item'] == item]
print(f'Number of rows for item {item}: {len(df2)}')
assessorAnalysis(df2, item, colScore='Weighted Score')

# now for 533
item = '533'
df2 = assessorDf[assessorDf['Item'] == item]
print(f'Number of rows for item {item}: {len(df2)}')
assessorAnalysis(df2, item, colScore='% Yes')

# now for 532
item = '532'
df2 = assessorDf[assessorDf['Item'] == item]
print(f'Number of rows for item {item}: {len(df2)}')
assessorAnalysis(df2, item, colScore='Weighted Score')

# now for 577
item = '577'
df2 = assessorDf[assessorDf['Item'] == item]
print(f'Number of rows for item {item}: {len(df2)}')
assessorAnalysis(df2, item, colScore='% Yes')

assessors = assessorDf['assessor_name'].unique()
for ass in assessors:
    assDf = assessorDf[assessorDf['assessor_name']==ass]

In [ ]:
# Examiner analysis:
import statsmodels.api as sm
from statsmodels.stats.multicomp import MultiComparison
import matplotlib.pyplot as plt
from scipy.stats import f_oneway, kruskal
from scipy.stats import pearsonr
from statsmodels.stats.multicomp import pairwise_tukeyhsd

df = pd.read_excel(f'{folder}\\miniCEX BOH scoresheet.xlsx')
# display(df.head())
for examiner in df['assessor_name'].unique():
    examinerDf = df[df['assessor_name'] == examiner]
    print(f'Examiner: {examiner}')
    # display(examinerDf.head())




# 1. Bar plot of average weighted score per examiner
plt.figure(figsize=(8, 5))
ax = sns.barplot(data=df, x='assessor_name', y='Weighted Score', estimator='mean', ci=None)
plt.title("Average Weighted Score per Examiner")
plt.ylabel("Average Weighted Score")
plt.xlabel("Examiner")
plt.tight_layout()
# annotate the bars with the mean score
# Annotate each bar with its height (mean score)
for p in ax.patches:
    height = p.get_height()
    ax.annotate(f'{height:.1f}', (p.get_x() + p.get_width() / 2., height),
                ha='center', va='bottom', fontsize=10)
plt.show()


# 2. Box plot of weighted scores per examiner
plt.figure(figsize=(8, 5))
sns.boxplot(data=df, x='assessor_name', y='Weighted Score')
plt.title("Score Distribution (Boxplot) by Examiner")
plt.ylabel("Weighted Score")
plt.xlabel("Examiner")
plt.tight_layout()
plt.show()

# 3. Distribution plot of Weighted Score per examiner
plt.figure(figsize=(10, 6))
sns.kdeplot(data=df, x='Weighted Score', hue='assessor_name', linestyle='--')
# a dotted kde for the overall distribution
# sns.kdeplot(data=df, x='Weighted Score', color='black', linestyle='-', label='Overall Distribution')
plt.title("Distribution of Weighted Scores per Examiner")
plt.xlabel("Weighted Score")
plt.tight_layout()
plt.show()

# ES v/s  Weighted Score plot
# Set up the plot
# Create subplots for each assessor
unique_assessors = df['assessor_name'].unique()
num_assessors = len(unique_assessors)
fig, axes = plt.subplots(num_assessors, 1, figsize=(8, 3 * num_assessors), sharex=True)
correlation_summary = []
for ax, assessor in zip(axes, unique_assessors):
    assessor_df = df[df['assessor_name'] == assessor]
        # Compute correlation
    if len(assessor_df) > 1:
        r, p = pearsonr(assessor_df['ES'], assessor_df['Weighted Score'])
    else:
        r, p = float('nan'), float('nan')
    
    # Store stats
    correlation_summary.append({
        'Assessor': assessor,
        'Pearson r': round(r, 3),
        'p-value': round(p, 3),
        'n': len(assessor_df)
    })
    
    sns.regplot(data=assessor_df, x='ES', y='Weighted Score', ci=None, ax=ax, color='blue', marker='o')
    ax.set_title(f'{assessor}\nPearson r={r:.2f}, p={p:.3f}, n={len(assessor_df)}')
    ax.set_xlabel('Entrustment Score (ES)')
    ax.set_ylabel('Weighted Score')
    ax.set_ylim(40, 105)
    ax.set_xlim(0.8, 4.2)
    ax.set_yticks(range(40, 110, 10))
    ax.set_xlabel('')
    ax.set_xticks(range(1, 5))
    ax.grid(True)
axes[-1].set_xlabel('Entrustment Score (ES)') 
plt.tight_layout()
plt.show()




# Prepare data per examiner
grouped_scores = [group['Weighted Score'].dropna().values for name, group in df.groupby('assessor_name')]

# Perform One-Way ANOVA
anova_stat, anova_p = f_oneway(*grouped_scores)

# Perform Kruskal-Wallis H-test (non-parametric alternative to ANOVA)
kruskal_stat, kruskal_p = kruskal(*grouped_scores)

# Summary of results
statistical_summary = pd.DataFrame({
    'Test': ['One-Way ANOVA', 'Kruskal-Wallis H'],
    'Test Statistic': [anova_stat, kruskal_stat],
    'p-value': [anova_p, kruskal_p]
})

display(statistical_summary)


# Tukey HSD test for multiple comparisons
df['Weighted Score'] = pd.to_numeric(df['Weighted Score'], errors='coerce')
tukey_df = df[['Weighted Score', 'assessor_name']].dropna()

# Perform Tukey HSD
tukey_result = pairwise_tukeyhsd(endog=tukey_df['Weighted Score'],
                                 groups=tukey_df['assessor_name'],
                                 alpha=0.05)

# Extract results into DataFrame
tukey_summary = tukey_result.summary()
tukey_data = tukey_summary.data[1:]  # skip header row
tukey_columns = tukey_summary.data[0]

tukey_summary_df = pd.DataFrame(tukey_data, columns=tukey_columns)
display(tukey_summary_df)

# Prepare data for Tukey HSD plot
multi_comp = MultiComparison(df['Weighted Score'], df['assessor_name'])
tukey_plot = multi_comp.tukeyhsd()
# Tukey plot
fig = tukey_plot.plot_simultaneous()
plt.title('Tukey HSD: Examiner Comparison')
plt.xlabel('Mean Difference in Weighted Score')
plt.tight_layout()
plt.show()



### Student Report creation mini cex

In [ ]:
IC_BOH_fullnames = {
    "MC1": "Performs hand hygiene in accordance with the five moments of hand hygiene.",
    "MC2": "Performs hand rub and hand washing technique in accordance with the World Health Organization guidelines.",
    "MC3": "Dons/doffs PPE in accordance with the Australian Commission on Safety and Quality in Health Care guidelines.",
    "MC4": "Follows record keeping requirements (places instrument tracking sticker onto tracking sheet).",
    "MC5": "Checks instrument expiry.",
    "MC6": "Checks sterilisation was successful by colour change indicator.",
    "MC7": "Peels instrument packaging open and places instruments onto bracket table.",
    "MC8": "Transports instruments safely, with sharps pointing towards the floor.",
    "MC9": "Adjusts clinician chair correctly.",
    "MC10": "Maintains good posture, positioning of self, patient, and bracket tray.",
    "MC11": "Demonstrates safe management and disposal of sharps.",
    "MC12": "Disposes of waste into appropriate receptacle.",
    "MC13": "Takes out detergent wipes.",
    "MC14": "Wipes non-clinical area from high to low.",
    "MC15": "Wipes operator and DA’s chair from back to front.",
    "MC16": "Wipes dental unit from top to bottom, cleanest to dirtiest.",
    "MC17": "Flushes lines.",
    "MC18": "Sets up bay (places bibs and glasses out)."
}
df = pd.read_excel(f'{folder}\\all data scores 2.xlsx')
rubricRef = pd.read_excel('2025\Rubric Reference Table.xlsx')
rubricRef.set_index('Score', inplace=True)
folder, file, ext = getFolderandFileName(f'{folder}\\all data scores.xlsx')
df = df.replace('_x000D_', '', regex=True)
dfboh = df[df['cohort'] == 'BOH1']
ids = dfboh[colId].unique()
importantCols = [colName, colId,  colDate, colAssessorName, colAssessorFeedback, colCI]
dfboh[rubricCols] = dfboh[rubricCols].astype('Int64')
for id in ids:
    studentDoc = SimpleDocTemplate(f'{folder}\\Student Reports\\{id}.pdf', pagesize=pageSize, rightMargin=rightMargin, leftMargin=leftMargin, topMargin=topMargin, bottomMargin=bottomMargin)
    elements = []
    studentDf = dfboh[dfboh[colId] == id]
    studentName = studentDf[colName].values[0]
    # studentDf = studentDf[impCols]
    studentDf = studentDf[studentDf['supervisor_data'].notna()]
    # display(studentDf.head())
    # convert supervisor_data to json
    studentDf['supervisor_data'] = studentDf['supervisor_data'].apply(lambda x: json.loads(x))
    studentDf['Scores'] = studentDf['Scores'].apply(lambda x: json.loads(x))
    display(studentDf.head())
    for i, row in studentDf.iterrows():

        # for all the important columns display column name and value
        elements.append(Paragraph(f'Form {i+1}: {row[colDate]}', subheadingStyle))
        # elements.append(Paragraph(f'Role: {row["role"]}', subsubheadingStyle))
        elements.append(Spacer(1, 10))
        for col in importantCols:
            if pd.isna(row[col]) or row[col] == 'nan':
                continue
            # print(f'{col}: {row[col.lower()]}')
            elements.append(Paragraph(f'{col.strip()}', smallsubsubheadingStyleL))
            elements.append(Spacer(1, 6))
            text = str(row[col]).strip().replace('\n', '<br/>')
            # text = row[col].strip()
            # remove non-ascii characters
            text = re.sub(r'[^\x00-\x7F]+', '', text)

            elements.append(Paragraph(f'{text}', tableTextStyleL))
            elements.append(Spacer(1, 12))

        for col in rubricCols:
            if pd.isna(row[col]) or row[col] == 'nan':
                continue
            # print(f'{col}: {row[col.lower()]}')
            elements.append(Paragraph(f'{col.strip()}', smallsubsubheadingStyleL))
            elements.append(Spacer(1, 6))
            text =f'Lvl {row[col]}: {rubricRef.loc[row[col], col]}'
            text = text.strip().replace('\n', '<br/>')
            # text = row[col].strip()
            # remove non-ascii characters
            text = re.sub(r'[^\x00-\x7F]+', '', text)

            elements.append(Paragraph(f'{text}', tableTextStyleL))
            elements.append(Spacer(1, 12))

        # create a table of the supervisor data
        evalDf = pd.DataFrame.from_dict(row['supervisor_data'], orient='index').T
        # display(evalDf.head())
        mcCols = [col for col in evalDf.columns if 'MC' in col]
        evalDf = evalDf[mcCols]
        evalDf = evalDf.T.reset_index()

        evalDf.columns = ['Checklist', 'Result']
        evalDf['Checklist'] = evalDf['Checklist'].map(lambda x: x.split('_')[-1])
        evalDf['Full Name'] = evalDf['Checklist'].map(IC_BOH_fullnames)
        evalDf = evalDf[['Checklist', 'Full Name', 'Result']]
        display(evalDf.head())        
        evalTable = createTable(evalDf, 'Marking Checklist', colRatio=[1, 5, 1], customTextCols=[1], bottomPadding=6, topPadding=6, cellHighlight=True,
                                tableTextStyle=tableTextStyleSmall)
        elements.append(evalTable)
        elements.append(Spacer(1, 12))
        scores = row['Scores']['IC-BOH']
        print(scores)
        scoreText = f"<b> Total Score: {scores['Total Score']}</b>"
        noteText = f"""In marking checklist each checklist item holds a different score weightage.<br/> Your total score is result of 
        your performance in marking checklist as well as your performance in the rubric. <br/>
        """ 
        elements.append(Paragraph(scoreText, tableTextStyleL))
        elements.append(Spacer(1, 12))
        elements.append(Paragraph(noteText, tableTextStyleL))
    studentDoc.build(elements)
    # break


### Time series and other reports

In [ ]:
# folder = '2025\\BOH2\\Form 1'
# folder = '2025/DDS2'
folder = '2025/BOH1'
df = pd.read_excel(f'{folder}\\all data scores.xlsx')
df['Scores'] = df['Scores'].apply(lambda x: json.loads(x))
display(df['Item Codes'].head())
print(df['Item Codes'].apply(type).head())
import ast
df['Item Codes'] = df['Item Codes'].apply(lambda x: ast.literal_eval(x) if isinstance(x, str) and x.startswith('[') else x)
print(df['Item Codes'].apply(type).head())
# check whether the item codes are being extracted as a list
dfSim = df[df['type'] == 'Simulation']
dfClinic = df[df['type'] == 'Clinic']
doc = SimpleDocTemplate(f'{folder}\\Score time series (all students).pdf', pagesize=pageSize, rightMargin = rightMargin, leftMargin = leftMargin, topMargin = topMargin, bottomMargin = bottomMargin)
timeSeriesElements = createTimeSeriesReport(df, 'Weighted Score')
doc.build(timeSeriesElements)

# sim and clinic time series
docSim = SimpleDocTemplate(f'{folder}\\Score time series (Simulation).pdf', pagesize=pageSize, rightMargin = rightMargin, leftMargin = leftMargin, topMargin = topMargin, bottomMargin = bottomMargin)
timeSeriesElements = createTimeSeriesReport(dfSim, 'Weighted Score')
docSim.build(timeSeriesElements)

docClin = SimpleDocTemplate(f'{folder}\\Score time series (Clinic).pdf', pagesize=pageSize, rightMargin = rightMargin, leftMargin = leftMargin, topMargin = topMargin, bottomMargin = bottomMargin)
timeSeriesElements = createTimeSeriesReport(dfClinic, 'Weighted Score')
docClin.build(timeSeriesElements)



In [ ]:
# # Create a doc=========================================================================================================================================================================
docScores = SimpleDocTemplate(f'{folder}\\Basic info report scores.pdf', pagesize=pageSize, rightMargin = rightMargin, leftMargin = leftMargin, topMargin = topMargin, bottomMargin = bottomMargin)
docScoresSim = SimpleDocTemplate(f'{folder}\\Basic info report scores Sim.pdf', pagesize=pageSize, rightMargin = rightMargin, leftMargin = leftMargin, topMargin = topMargin, bottomMargin = bottomMargin)
docScoresClin = SimpleDocTemplate(f'{folder}\\Basic info report scores Clin.pdf', pagesize=pageSize, rightMargin = rightMargin, leftMargin = leftMargin, topMargin = topMargin, bottomMargin = bottomMargin)
scoreElements, totalDf = createScoreTables(df)
docScores.build(scoreElements.copy())
scoreElementsSim, totalDfSim = createScoreTables(dfSim)
docScoresSim.build(scoreElementsSim.copy())
scoreElementsClin, totalDfClin = createScoreTables(dfClinic)
docScoresClin.build(scoreElementsClin.copy())
totalDf.to_excel(f'{folder}\\All student scores in a table.xlsx')

In [ ]:

doc = SimpleDocTemplate(f'{folder}\\Basic info report.pdf', pagesize=pageSize, rightMargin = rightMargin, leftMargin = leftMargin, topMargin = topMargin, bottomMargin = bottomMargin)
docSim = SimpleDocTemplate(f'{folder}\\Basic info report Sim.pdf', pagesize=pageSize, rightMargin = rightMargin, leftMargin = leftMargin, topMargin = topMargin, bottomMargin = bottomMargin)
docClin = SimpleDocTemplate(f'{folder}\\Basic info report Clin.pdf', pagesize=pageSize, rightMargin = rightMargin, leftMargin = leftMargin, topMargin = topMargin, bottomMargin = bottomMargin)
elements = []
simElements = createData(dfSim, 'Simulation')
elements.extend(simElements)
docSim.build(simElements.copy())

# now for clinic data
# clinElements = createData(dfClinic, 'Clinic') 
# patientCounts = getNPatients(dfClinic)
# patientCountsTable = createTable(patientCounts, 'Patient Counts', colRatio=[1.3, 1.7, 1], bottomPadding=8, topPadding=8)
# clinElements.append(patientCountsTable)
# text = 'I have used the data in patient_complexity to get the number of patients seen by each student as there is no other field to get the number of patients seen. ' 
# clinElements.append(Paragraph(text, tableTextStyle))
# docClin.build(clinElements.copy())
# elements.extend(clinElements)


elements.append(PageBreak())
doc.build(elements.copy())

### BOH3 and DDS4 time series

In [ ]:
## BOH3 scores
workbookpath = '2025\BOH3+DDS4\Session 4\\2025 BOH3 and DDS4 CAF.xlsx'
folder, file, ext = getFolderandFileName(workbookpath)
df = pd.read_excel(workbookpath)
fullnameDict = { col: df.loc[0, col] for col in df.columns}
df.drop(index=0, inplace=True)

In [ ]:
df.columns = df.columns.str.strip()
print(df.columns)

beforecolumns = [
    "Given name", "Family Name", "Student ID", "Email",
    "Date", "Cohort", "Rotation", "Clinic", "Role"
]

evalCols = [col for col in df.columns if 'Evaluation#' in col]
supEvalCols = [col for col in evalCols if 'Evaluation#2' in col]
colES = 'Entrustment'
colCI = 'Clinical Incident'
colCIReason = 'CI Explanation'
colEdu = 'Edu Name'
colFeedback = ['Student Reflection',	'Edu Feedback']
df = df[beforecolumns + evalCols +  [colES, colCI, colCIReason, colEdu] + colFeedback]
display(df.head())
cohort = 'DDS4'


In [ ]:
dfOperator = df[df['Role'] == 'Operator']
dfOperator['#Yes'] = df.apply(lambda x: x[supEvalCols].str.contains('Yes').sum(), axis=1)
dfOperator['#No'] = df.apply(lambda x: x[supEvalCols].str.contains('No').sum(), axis=1)
dfOperator['#NA'] = df.apply(lambda x: x[supEvalCols].str.contains('NA').sum(), axis=1)
dfOperator['%Yes'] = (dfOperator['#Yes'] / (dfOperator['#Yes'] + dfOperator['#No'])*100).round(2)
dfOperator[colES] = dfOperator[colES].str.extract('Lvl (\d+)').astype('Int64')
dfOperator.sort_values(by=['Family Name', 'Given name'], inplace=True)

In [ ]:
dfOperator = dfOperator[dfOperator['Cohort'] == cohort]

In [ ]:
clinicShortforms = {
    "RDHM": "RDHM",
    "MDC": "MDC",
    "YOUR Community ": "YOUR",
    "La Trobe Community ": "LaTrobe",
    "Banyule ": "Banyule",
    "IPC ": "IPC",
    "Health Ability ": "HAbility",
    "EACH": "EACH",
    "Echuca Regional Health ": "Echuca",
    "Link Health ": "Link",
    "VAHS": "VAHS",
    "Cohealth ": "Cohealth",
    "Other": "Other",
    "Goulburn Valley Health ": "GVH",
    "Cobram District CHC ": "Cobram",
    "Rumbalara": "Rumbalara",
    "North Richmond Community Health": "NRCH",
    "Northeast Health ": "NEHealth"
}
display(dfOperator.head())
print(dfOperator['Clinic'].unique())
colScore = '%Yes'
def annotateClinicLabels(ax, df, xCol, yCol, labelCol, shortformDict):
    offsetCounter = defaultdict(int)
    for _, row in df.iterrows():
        key = (row[xCol], row[yCol])
        if pd.isna(row[xCol]) or pd.isna(row[yCol]):
            continue
        offset = offsetCounter[key] * 5
        offsetCounter[key] += 1
        label = shortformDict.get(row[labelCol], row[labelCol])
        ax.annotate(label,
                    (row[xCol], row[yCol]),
                    textcoords="offset points", xytext=(0, 5 + 2 * offset),
                    ha='center', fontsize=6)
        
def createTimeSeries(studentDf, studentName, id, colScore):
    fig, ax = plt.subplots(figsize=(14, 7))
    ax.scatter(studentDf['Date'], studentDf[colScore], color='blue')
    ax.set_xticklabels(ax.get_xticklabels(), rotation=90)
    annotateClinicLabels(ax, studentDf, 'Date', colScore, 'Clinic', clinicShortforms)
    title = f'{studentName} ({id})'
    ax.set_title(title)
    ax.set_xlabel("Date")
    ax.set_ylabel("Score (% Yes)")
    ax.grid(True, linestyle='--', alpha=0.5)
    ax.tick_params(axis='x', rotation=45)
    ax.set_ylim(0.8*studentDf[colScore].min(), 1.2*studentDf[colScore].max())
    ax.set_yticks(range(int((studentDf[colScore].min() - 1)/10)*10, int(studentDf[colScore].max() + 1), int(max(studentDf[colScore].max()//10, 1))))
    fig.tight_layout()
    return fig


docTimeSeries = SimpleDocTemplate(f'{folder}\\{cohort} Time series report.pdf', pagesize=pageSize,
                                   rightMargin = rightMargin, leftMargin = leftMargin, topMargin = topMargin, bottomMargin = bottomMargin)   
timeSeriesElements = []
for id in dfOperator['Student ID'].unique():
    studentDf = dfOperator[dfOperator['Student ID'] == id]
    studentName = studentDf['Family Name'].values[0] + ' ' + studentDf['Given name'].values[0]
    print(f'Student: {studentName} ({id})')
    studentDf['Date'] = pd.to_datetime(studentDf['Date'], format='mixed')
    studentDf.sort_values(by='Date', inplace=True)
    studentDf['Date'] = studentDf['Date'].dt.strftime('%d %b')
    timeSeriesfig = createTimeSeries(studentDf, studentName, id, colScore)
    timeSeriesImg = addPlotImage(timeSeriesfig, 0.9)
    # now entrustment time series
    label = colES
    fig, ax = plt.subplots(figsize=(14, 7))
    ax.plot(studentDf[colDate], studentDf[label], label=label, marker='o', color = 'orange')
    annotateClinicLabels(ax, studentDf, colDate, label, 'Clinic', clinicShortforms)
    ax.set_title('Entrustment Time Series')
    ax.set_xlabel('Date')
    ax.set_ylabel('Entrustment')
    ax.set_ylim(0, studentDf[label].max() + 0.5)
    ax.tick_params(axis='x', rotation=45)
    ax.grid(True, linestyle='--', alpha=0.5)
    ax.set_yticks(range(0, int(studentDf[label].max()+1), 1))
    ax.set_yticklabels(range(0, int(studentDf[label].max()+1), 1))
    plt.tight_layout()
    ax.set_title(f'Entrustment Level for {studentName} ({id})')
    esTimeSeriesImg = addPlotImage(fig, 0.9)
    timeSeriesElements.append(KeepTogether([timeSeriesImg, Spacer(1, 12), esTimeSeriesImg]))
    timeSeriesElements.append(PageBreak())


    plt.show()
    # break

docTimeSeries.build(timeSeriesElements.copy())

In [ ]:
results = []
for id in dfOperator['Student ID'].unique():
    # figure out which of the Evaluation# columns have the lowest and highest scores
    studentDf = dfOperator[dfOperator['Student ID'] == id]
    studentName = studentDf['Family Name'].values[0] + ' ' + studentDf['Given name'].values[0]
    print(f'Student: {studentName} ({id})')
    studentDf['Date'] = pd.to_datetime(studentDf['Date'], format='mixed')
    studentDf.sort_values(by='Date', inplace=True)
    studentDf['Date'] = studentDf['Date'].dt.strftime('%d %b')
    # get the columns that have the lowest and highest scores
    colScores = [col for col in studentDf.columns if 'Evaluation#2' in col]
    studentDf[colScores] = studentDf[colScores].replace({'Yes': 1, 'No': 0, 'NA': np.nan})
    meanScores = studentDf[colScores].mean()
    # Top 3 and bottom 3 using full names
    best3 = meanScores.sort_values(ascending=False).head(3)
    worst3 = meanScores.sort_values().head(3)

    results.append({
        'ID': id,
        'Name': studentName,
        'Best 3': '<br/> '.join([fullnameDict.get(col, col).split(' - ')[-1].split('\n')[0] for col in best3.index]),
        'Best<br/>Scores': '<br/> '.join([str(int(x*100)) for x in best3.values]),
        'Worst 3': '<br/> '.join([fullnameDict.get(col, col).split(' - ')[-1].split('\n')[0] for col in worst3.index]),
        'Worst<br/>Scores': '<br/> '.join([str(int(x*100)) for x in worst3.values]),
    })
    # break
# convert results to a dataframe
resultsDf = pd.DataFrame(results)
resultsTable = createTable(resultsDf, 'Best and Worst areas of students', colRatio=[1, 1, 4, 1, 4, 1], customTextCols=[1, 2, 3, 4, 5], bottomPadding=12, topPadding=12,
                           tableTextStyle=tableTextStyleSmall)
table = resultsTable._content[2]
headerRow = table._cellvalues[0]
tableTextStyleLarge.fontName = 'Helvetica-Bold'
for i in range(len(headerRow)):
    headerText = str(headerRow[i])
    wrappedPara = Paragraph(headerText, tableTextStyleLarge)
    table._cellvalues[0][i] = wrappedPara
# change the header to wrap text
resultElements = []
resultElements.append(resultsTable)
docResults = SimpleDocTemplate(f'{folder}\\BOH3 Best and Worst areas of students.pdf', pagesize=pageSize,
                                   rightMargin = rightMargin, leftMargin = leftMargin, topMargin = topMargin, bottomMargin = bottomMargin)
docResults.build(resultElements.copy())
display(resultsDf.head())

## DDS2

## BOH3 scores

In [ ]:
workbookpath = '2025\BOH3+DDS4\Session 4\\2025 BOH3 and DDS4 CAF.xlsx'
folder, file, ext = getFolderandFileName(workbookpath)
df = pd.read_excel(workbookpath)
fullnameDict = { col: df.loc[0, col] for col in df.columns}
df.drop(index=0, inplace=True)


In [ ]:
df.columns = df.columns.str.strip()
print(df.columns)

beforecolumns = [
    "Given name", "Family Name", "Student ID", "Email",
    "Date", "Cohort", "Rotation", "Clinic", "Role"
]

evalCols = [col for col in df.columns if 'Evaluation#' in col]
supEvalCols = [col for col in evalCols if 'Evaluation#2' in col]
colES = 'Entrustment'
colCI = 'Clinical Incident'
colCIReason = 'CI Explanation'
colEdu = 'Edu Name'
colFeedback = ['Student Reflection',	'Edu Feedback']
df = df[beforecolumns + evalCols +  [colES, colCI, colCIReason, colEdu] + colFeedback]
display(df.head())

In [ ]:
dfOperator = df[df['Role'] == 'Operator']
dfOperator['#Yes'] = df.apply(lambda x: x[supEvalCols].str.contains('Yes').sum(), axis=1)
dfOperator['#No'] = df.apply(lambda x: x[supEvalCols].str.contains('No').sum(), axis=1)
dfOperator['#NA'] = df.apply(lambda x: x[supEvalCols].str.contains('NA').sum(), axis=1)
dfOperator['%Yes'] = (dfOperator['#Yes'] / (dfOperator['#Yes'] + dfOperator['#No'])*100).round(2)
dfOperator[colES] = dfOperator[colES].str.extract('Lvl (\d+)').astype('Int64')
display(dfOperator.head())

In [ ]:
# remove codes of the form 524_MCx and 578_MCx

def compare_supervisors(studentDf):
    if len(studentDf) != 2:
        print("Error: The student must have exactly two rows for comparison.")
        return None
    
    row1, row2 = studentDf.iloc[0], studentDf.iloc[1]
    
    # Identify columns where neither row has NA
    valid_cols = [col for col in assessormcCols if row1[col] != 'NA' and row2[col] != 'NA']
    
    # Filter to only Yes/No columns
    yes_no_cols = [col for col in valid_cols if studentDf[col].isin(['Yes', 'No']).all()]
    
    # Count differences
    diff_yes_to_no = sum(row1[col] == 'Yes' and row2[col] == 'No' for col in yes_no_cols)
    diff_no_to_yes = sum(row1[col] == 'No' and row2[col] == 'Yes' for col in yes_no_cols)
    
    # Count how many more Yes answers the first supervisor has over the second
    yes_first_more = sum(row1[col] == 'Yes' and row2[col] == 'No' for col in yes_no_cols) - \
                     sum(row1[col] == 'No' and row2[col] == 'Yes' for col in yes_no_cols)

    return {
        "Yes to No": diff_yes_to_no,
        "No to Yes": diff_no_to_yes,
        "Yes (First Supervisor) More By": yes_first_more
    }

def createAssessorSummary(df, assessormcCols):
    assessor_value_counts = {}
    for assessor in df['assessor_name'].unique():
        assessorDf = df[df['assessor_name'] == assessor]
        # Count occurrences of each unique value across all assessor MC columns
        value_counts = assessorDf[assessormcCols].apply(pd.Series.value_counts).sum(axis=1).to_dict()
        # add value for number of assessments
        value_counts['Total Forms'] = len(assessorDf)
        value_counts['entrustment'] = assessorDf['entrustment'].value_counts().to_dict()
        # Store result
        assessor_value_counts[assessor] = value_counts

    # Convert results to DataFrame for better visualization
    assessor_summary_df = pd.DataFrame.from_dict(assessor_value_counts, orient='index').fillna(0)
    assessor_summary_df['Total'] = assessor_summary_df.sum(axis=1)
    # total of Yes and No
    assessor_summary_df['YesNoTotal'] = assessor_summary_df['Yes'] + assessor_summary_df['No']
    assessor_summary_df['Leniency'] = assessor_summary_df['Yes'] / assessor_summary_df['YesNoTotal']
    # sort on linency
    assessor_summary_df.sort_values(by='Leniency', inplace=True, ascending=False)
    return assessor_summary_df


### Standard Setting

In [ ]:
ssFile = '2025\StandardSetting.xlsx'
data524_578file = '2025\DDS2\Michael\michaelData 524+578.xlsx'
data533_577file = '2025\DDS2\Michael\michaelData 533+577.xlsx'
data524_578 = pd.read_excel(data524_578file)
folder, file, ext = getFolderandFileName(data524_578file)
data533_577 = pd.read_excel(data533_577file)
ss1 = pd.read_excel(ssFile, sheet_name= 'MW SIM Adhesive List')
marking_dict1 = ss1.set_index("Marking Checklist")["Importance"].to_dict()
ss2 = pd.read_excel(ssFile, sheet_name = '577')
marking_dict2 = ss2.set_index("Marking Checklist")["Importance"].to_dict()
ss3 = pd.read_excel(ssFile, sheet_name = '578')
marking_dict3 = ss3.set_index("Marking Checklist")["Importance"].to_dict()

# change dict keys to assessor_code_MC\d
def changeKey(d, code):
    newd = {}
    for key, value in d.items():
        newkey = f'assessor_{code}_{key}'
        newd[newkey] = value
    return newd
marking_dict524 = changeKey(marking_dict1, '524')
marking_dict533 = changeKey(marking_dict1, '533')
marking_dict577 = changeKey(marking_dict2, '577')
marking_dict578 = changeKey(marking_dict3, '578')
joint_dict = {**marking_dict524, **marking_dict533, **marking_dict577, **marking_dict578}

In [ ]:
def defineVars(df):
    pecItems  = ['positioning', 'Consent', 'Record', 'infection']
    rubricCols = ['time_mgmt', 'communication', 'professionalism', 'entrustment']
    mcCols = [col for col in df.columns if 'MC' in col and 'positioning' not in col and 'Consent' not in col and 'Record' not in col and 'infection' not in col]
    pecCols = [col for col in df.columns if 'positioning' in col or 'Consent' in col or 'Record' in col or 'infection' in col]
    studentmcCols = [col for col in mcCols if 'student' in col]
    assessormcCols = [col for col in mcCols if 'assessor' in col]

    otherCols = [col for col in df.columns if col not in mcCols and col not in rubricCols and col not in pecCols]
    print(otherCols)
    otherfullnamedict = {'student_name': 'Student Name', 'assessor_name': 'Assessor Name', 'date': 'Date', 'cohort': 'Cohort', 'subject': 'Subject', 'type': 'Type',
                        'time_mgmt': 'Time Management', 'communication': 'Communication', 'professionalism': 'Professionalism', 'entrustment': 'Entrustment',
                        'student_feedback': 'Student Feedback', 'assessor_feedback': 'Assessor Feedback', 'clinical_incident': 'Clinical Incident',
                        'patient_complexity': 'Complexity', 'Consent': 'Consent'}
    return mcCols, pecCols, studentmcCols, assessormcCols, otherCols, otherfullnamedict, rubricCols

In [ ]:
# 524 and 578
data524_578.drop(columns = ['student_524_MC3',	'student_524_MC4', 'assessor_524_MC3', 'assessor_524_MC4'], inplace=True, errors='ignore')

# get unique students
unique_students = data524_578['student_name'].nunique()
print(f"Unique students: {unique_students}")   
studentList = data524_578['student_name'].unique()
# print(studentList)
mcCols, pecCols, studentmcCols, assessormcCols, otherCols, otherfullnamedict, rubricCols = defineVars(data524_578)
data524_578.drop(studentmcCols, axis=1, inplace=True)
# Function to fill NaN values from the other row
# Function to fill NaN values from the other row in a group
def fill_nan_from_other_row(series):
    return series.fillna(method='ffill').fillna(method='bfill')

# Apply the function correctly using transform() instead of apply()
data524_578[assessormcCols] = data524_578.groupby("student_name")[assessormcCols].transform(fill_nan_from_other_row)
for student in studentList:
    studentDf = data524_578[data524_578['student_name'] == student]
    # for each student we have two dates, for the Nan values in one date, we can fill with the other date
    # display(studentDf)

# marking_dict524 is importance dict for each MC question for 524 with assessor_524_MC\d: Importance as key value pair
# marking_dict533 is importance dict for each MC question for 533 with assessor_533_MC\d: Importance as key value pair
# marking_dict577 is importance dict for each MC question for 577 with assessor_577_MC\d: Importance as key value pair
# marking_dict578 is importance dict for each MC question for 578 with assessor_578_MC\d: Importance as key value pair

# importance 10 is critical, 7-9 are important, 4-6 are moderate, 1-3 are minor

# add a column to see whether critical was marked Yes
def getCritical(row, marking_dict, valueMatch):
    counter = 0 
    for key, value in marking_dict.items():
        if key not in row:
            continue
        if value in [10]:
            if row[key]==valueMatch:
                counter += 1
    return counter

data524_578['#CriticalYes'] = data524_578.apply(lambda x: getCritical(x, joint_dict, 'Yes'), axis=1)
data524_578['#CriticalNo'] = data524_578.apply(lambda x: getCritical(x, joint_dict, 'No'), axis=1)
# Add a column to calculate the percentage of critical Yes responses, handling zero denominator
data524_578['%CriticalYes'] = data524_578.apply(
    lambda x: (x['#CriticalYes'] / (x['#CriticalYes'] + x['#CriticalNo']) * 100) if (x['#CriticalYes'] + x['#CriticalNo']) != 0 else np.nan,
    axis=1
)

# add column to see how many important were marked Yes, get the counts
def getImportant(row, marking_dict, valueMatch):
    counter = 0
    for key, value in marking_dict.items():
        if key not in row:
            continue
        if value in [7, 8, 9]:
            if row[key]==valueMatch:
                counter += 1
    return counter
data524_578['#ImportantYes'] = data524_578.apply(lambda x: getImportant(x, joint_dict, 'Yes'), axis=1)
data524_578['#ImportantNo'] = data524_578.apply(lambda x: getImportant(x, joint_dict, 'No'), axis=1)
data524_578['%ImportantYes'] = data524_578.apply(
    lambda x: (x['#ImportantYes'] / (x['#ImportantYes'] + x['#ImportantNo']) * 100) if (x['#ImportantYes'] + x['#ImportantNo']) != 0 else np.nan,
    axis=1
)
# add column to see how many moderate were marked Yes, get the counts
def getModerate(row, marking_dict, valueMatch):
    counter = 0
    for key, value in marking_dict.items():
        if key not in row:
            continue
        if value in [4, 5, 6]:
            if row[key]==valueMatch:
                counter += 1
    return counter
data524_578['#ModerateYes'] = data524_578.apply(lambda x: getModerate(x, joint_dict, 'Yes'), axis=1)
data524_578['#ModerateNo'] = data524_578.apply(lambda x: getModerate(x, joint_dict, 'No'), axis=1)
data524_578['%ModerateYes'] = data524_578.apply(
    lambda x: (x['#ModerateYes'] / (x['#ModerateYes'] + x['#ModerateNo']) * 100) if (x['#ModerateYes'] + x['#ModerateNo']) != 0 else np.nan,
    axis=1
)


# add column to see how many minor were marked Yes, get the counts
def getMinor(row, marking_dict, valueMatch):
    counter = 0
    for key, value in marking_dict.items():
        if key not in row:
            continue
        if value in [1, 2, 3]:
            if row[key]==valueMatch:
                counter += 1
    return counter
data524_578['#MinorYes'] = data524_578.apply(lambda x: getMinor(x, joint_dict, 'Yes'), axis=1)
data524_578['#MinorNo'] = data524_578.apply(lambda x: getMinor(x, joint_dict, 'No'), axis=1)
data524_578['%MinorYes'] = data524_578.apply(
    lambda x: (x['#MinorYes'] / (x['#MinorYes'] + x['#MinorNo']) * 100) if (x['#MinorYes'] + x['#MinorNo']) != 0 else np.nan,
    axis=1
)
display(data524_578.head()) 

doc = SimpleDocTemplate(f'{folder}\\524+578 student eval.pdf', pagesize=pageSize, rightMargin = rightMargin, leftMargin = leftMargin, topMargin = topMargin, bottomMargin = bottomMargin)
elements = []
# create a stacked bar chart for important Yes, No for all students
fig, ax = plt.subplots(figsize=(figSize[0], figSize[1]))
plotdf = data524_578[['student_name', '#CriticalYes', '#CriticalNo', '#ImportantYes', '#ImportantNo', '#ModerateYes', '#ModerateNo', '#MinorYes', '#MinorNo']]
plotdf = plotdf.groupby('student_name').mean()
# plotdf.set_index('student_name', inplace=True)
plotdf[['#ImportantYes', '#ImportantNo']].plot(kind='barh', stacked=True, ax=ax)
img = addPlotImage(fig)
# elements.append(img)

statdf = data524_578[['student_name', '%CriticalYes', '%ImportantYes', '%ModerateYes', '%MinorYes']]
statdf = statdf.groupby('student_name').mean()
statdf.sort_values(by=['%CriticalYes', '%ImportantYes', '%ModerateYes', '%MinorYes'], ascending=False, inplace=True)
# round the values
statdf = statdf.round(2)
# display(statdf)
# statdf.to_excel(f'{folder}\\524+578 student eval.xlsx')
statdf.drop(columns=["%CriticalYes"], inplace=True)
statdf.reset_index(inplace=True)
stattable = createTable(statdf, 'Student Evaluation', colRatio=[1, 1, 1, 1])
elements.append(stattable)
doc.build(elements)

# create guttman of the whole data
guttmandf = data524_578.copy()
guttmandf = guttmandf.applymap(lambda x: 1 if x == 'Yes' else x)
guttmandf = guttmandf.applymap(lambda x: 0 if x == 'No' else x)
guttmandf = guttmandf.applymap(lambda x: np.nan if x == 'NA' else x)
# aggregate the data by student name sum of MC columns and take mean for rubric columns and first row for other columns, join the string in 'assessor_feedback'
agg_dict = {
    'assessor_feedback': lambda x: ','.join(x),
    'clinical_incident': 'first',
    'time_mgmt': 'mean',
    'communication': 'mean',
    'professionalism': 'mean',
    'entrustment': 'mean',
}

# Add assessor MC columns to aggregate them using 'sum'
agg_dict.update({col: 'sum' for col in assessormcCols})
leftovercols = [col for col in guttmandf.columns if col not in agg_dict.keys()]
agg_dict.update({col: 'first' for col in leftovercols})
guttmandf['assessor_feedback'] = guttmandf['assessor_feedback'].astype(str)
# Apply aggregation
guttmandf = guttmandf.groupby('student_name').agg(agg_dict)
guttmandf['MC Score'] = guttmandf[assessormcCols].sum(axis=1)
# get columnwise total for mcCols
colTotal = guttmandf[assessormcCols].sum(skipna=True)
guttmandf.loc['Column Total'] = pd.Series(colTotal, index=assessormcCols)

# sort columns by total
guttmandf = guttmandf[guttmandf.loc['Column Total'].sort_values(ascending=False).index]
# sort rows by MC Score
guttmandf = guttmandf.sort_values(by='MC Score', ascending=False)
display(guttmandf)
# guttmandf.to_excel(f'{folder}\\524+578 guttman.xlsx')


In [ ]:
# for 533 and 577
data533_577.drop(columns = ['student_533_MC13', 'student_533_MC11', 'assessor_533_MC12', 'assessor_533_MC7'], inplace=True, errors='ignore')
data533_577.drop(columns = ['student_577_MC3', 'student_577_MC4'], inplace=True, errors='ignore')

# get unique students
unique_students = data533_577['student_name'].nunique()
print(f"Unique students: {unique_students}")   
studentList = data533_577['student_name'].unique()
mcCols, pecCols, studentmcCols, assessormcCols, otherCols, otherfullnamedict, rubricCols = defineVars(data533_577)
data533_577.drop(studentmcCols, axis=1, inplace=True)

# Function to fill NaN values from the other row in a group
def fill_nan_from_other_row(series):
    return series.fillna(method='ffill').fillna(method='bfill')

# Apply the function correctly using transform() instead of apply()
data533_577[assessormcCols] = data533_577.groupby("student_name")[assessormcCols].transform(fill_nan_from_other_row)
for student in studentList:
    studentDf = data533_577[data533_577['student_name'] == student]

# add a column to see whether critical was marked Yes
data533_577['#CriticalYes'] = data533_577.apply(lambda x: getCritical(x, joint_dict, 'Yes'), axis=1)
data533_577['#CriticalNo'] = data533_577.apply(lambda x: getCritical(x, joint_dict, 'No'), axis=1)
data533_577['%CriticalYes'] = data533_577.apply(
    lambda x: (x['#CriticalYes'] / (x['#CriticalYes'] + x['#CriticalNo']) * 100) if (x['#CriticalYes'] + x['#CriticalNo']) != 0 else np.nan,
    axis=1
)

# add column to see how many important were marked Yes, get the counts
data533_577['#ImportantYes'] = data533_577.apply(lambda x: getImportant(x, joint_dict, 'Yes'), axis=1)
data533_577['#ImportantNo'] = data533_577.apply(lambda x: getImportant(x, joint_dict, 'No'), axis=1)
data533_577['%ImportantYes'] = data533_577.apply(
    lambda x: (x['#ImportantYes'] / (x['#ImportantYes'] + x['#ImportantNo']) * 100) if (x['#ImportantYes'] + x['#ImportantNo']) != 0 else np.nan,
    axis=1
)

# add column to see how many moderate were marked Yes, get the counts
data533_577['#ModerateYes'] = data533_577.apply(lambda x: getModerate(x, joint_dict, 'Yes'), axis=1)
data533_577['#ModerateNo'] = data533_577.apply(lambda x: getModerate(x, joint_dict, 'No'), axis=1)
data533_577['%ModerateYes'] = data533_577.apply(
    lambda x: (x['#ModerateYes'] / (x['#ModerateYes'] + x['#ModerateNo']) * 100) if (x['#ModerateYes'] + x['#ModerateNo']) != 0 else np.nan,
    axis=1
)

# add column to see how many minor were marked Yes, get the counts
data533_577['#MinorYes'] = data533_577.apply(lambda x: getMinor(x, joint_dict, 'Yes'), axis=1)
data533_577['#MinorNo'] = data533_577.apply(lambda x: getMinor(x, joint_dict, 'No'), axis=1)
data533_577['%MinorYes'] = data533_577.apply(
    lambda x: (x['#MinorYes'] / (x['#MinorYes'] + x['#MinorNo']) * 100) if (x['#MinorYes'] + x['#MinorNo']) != 0 else np.nan,
    axis=1
)
display(data533_577.head()) 

doc = SimpleDocTemplate(f'{folder}\\533+577 student eval.pdf', pagesize=pageSize, rightMargin = rightMargin, leftMargin = leftMargin, topMargin = topMargin, bottomMargin = bottomMargin)
elements = []
fig, ax = plt.subplots(figsize=(figSize[0], figSize[1]))
plotdf = data533_577[['student_name', '#CriticalYes', '#CriticalNo', '#ImportantYes', '#ImportantNo', '#ModerateYes', '#ModerateNo', '#MinorYes', '#MinorNo']]
plotdf = plotdf.groupby('student_name').mean()
plotdf[['#ImportantYes', '#ImportantNo']].plot(kind='barh', stacked=True, ax=ax)
img = addPlotImage(fig)

statdf = data533_577[['student_name', '%CriticalYes', '%ImportantYes', '%ModerateYes', '%MinorYes']]
statdf = statdf.groupby('student_name').mean()
statdf.sort_values(by=['%CriticalYes', '%ImportantYes', '%ModerateYes', '%MinorYes'], ascending=False, inplace=True)
statdf = statdf.round(2)
# statdf.drop(columns=["%CriticalYes"], inplace=True)
statdf.reset_index(inplace=True)
statdf.to_excel(f'{folder}\\533+577 student eval.xlsx')
stattable = createTable(statdf, 'Student Evaluation', colRatio=[1, 1, 1, 1])
elements.append(stattable)
doc.build(elements)

guttmandf = data533_577.copy()
guttmandf = guttmandf.applymap(lambda x: 1 if x == 'Yes' else x)
guttmandf = guttmandf.applymap(lambda x: 0 if x == 'No' else x)
guttmandf = guttmandf.applymap(lambda x: np.nan if x == 'NA' else x)
agg_dict = {
    'assessor_feedback': lambda x: ','.join(x),
    'clinical_incident': 'first',
    'time_mgmt': 'mean',
    'communication': 'mean',
    'professionalism': 'mean',
    'entrustment': 'mean',
}

agg_dict.update({col: 'sum' for col in assessormcCols})
leftovercols = [col for col in guttmandf.columns if col not in agg_dict.keys()]
agg_dict.update({col: 'first' for col in leftovercols})
guttmandf['assessor_feedback'] = guttmandf['assessor_feedback'].astype(str)
guttmandf = guttmandf.groupby('student_name').agg(agg_dict)
guttmandf['MC Score'] = guttmandf[assessormcCols].sum(axis=1)
colTotal = guttmandf[assessormcCols].sum(skipna=True)
guttmandf.loc['Column Total'] = pd.Series(colTotal, index=assessormcCols)
guttmandf = guttmandf[guttmandf.loc['Column Total'].sort_values(ascending=False).index]
guttmandf = guttmandf.sort_values(by='MC Score', ascending=False)
display(guttmandf)
guttmandf.to_excel(f'{folder}\\533+577 guttman.xlsx')

## BOH2

In [25]:
# workbookpath = '2025\BOH2\\Form 1\\all_data_combined.xlsx'
# workbookpath = '2025\BOH1\\all_data_combined.xlsx'
workbookpath  = '2025\DDS2\\all_data_combined.xlsx'
folder, file, ext = getFolderandFileName(workbookpath)
df = pd.read_excel(workbookpath, sheet_name='all_data_flat')
df.fillna('', inplace=True)
df.rename(columns={'student_number':'student_id'}, inplace=True)
df.drop(columns=['assessment_id'], inplace=True)
df['student_id'] = df['student_id'].astype(str)
with open('2025\sim_checklists.json') as f:
    simChecklist = json.load(f)
    simChecklist = {item['key']: item for item in simChecklist['result']}     # can get full name by key fields MCx
with open('2025\clinic_checklists.json') as f:
    clinicChecklist = json.load(f)
    clinicChecklist = {item['key']: item for item in clinicChecklist['result']}

pprint(simChecklist, indent=4)
pprint(clinicChecklist, indent=4)
pecItems  = ['positioning', 'Consent', 'Record', 'infection']
rubricCols = ['time_mgmt', 'communication', 'professionalism', 'entrustment']
mcCols = [col for col in df.columns if 'MC' in col and 'positioning' not in col and 'Consent' not in col and 'Record' not in col and 'infection' not in col]
pecCols = [col for col in df.columns if 'positioning' in col or 'Consent' in col or 'Record' in col or 'infection' in col]
studentmcCols = [col for col in mcCols if 'student' in col]
assessormcCols = [col for col in mcCols if 'assessor' in col]

otherCols = [col for col in df.columns if col not in mcCols and col not in rubricCols and col not in pecCols]
print(otherCols)
otherfullnamedict = {'student_name': 'Student Name', 'assessor_name': 'Assessor Name', 'date': 'Date', 'cohort': 'Cohort', 'subject': 'Subject', 'type': 'Type',
                     'time_mgmt': 'Time Management', 'communication': 'Communication', 'professionalism': 'Professionalism', 'entrustment': 'Entrustment',
                     'student_feedback': 'Student Feedback', 'assessor_feedback': 'Assessor Feedback', 'clinical_incident': 'Clinical Incident',
                     'patient_complexity': 'Complexity', 'Consent': 'Consent'}
mcColDict = {}
for col in mcCols:
    key = col.split('_')[1]
    if key not in mcColDict:
        mcColDict[key] = []
    mcColDict[key].append(col)
def get_items(row):
    items = []
    for key, cols in mcColDict.items():
        if any((not pd.isna(row[col])) and (row[col] not in ['', 'nan']) for col in cols):
            if key in pecItems:
                continue
            items.append(key)
    return items

df['Items'] = df.apply(get_items, axis=1)

# df = df[df['type'] == 'Clinic']
display(df.head())

{   '11-12': {   'fields': {   'MC1': 'Uses a relaxed modified pen grasp',
                               'MC10': 'Does not slip when probing',
                               'MC2': 'Selects correct working end to explore '
                                      'the specified area.',
                               'MC3': 'Inserts instrument with the terminal '
                                      'shank parallel to the long axis of the '
                                      'tooth.',
                               'MC4': 'Minimal pressure or displacement of '
                                      'gingiva at the cervical margin.',
                               'MC5': 'Adapts the tip to the tooth surface.',
                               'MC6': 'Applies controlled small V-shaped '
                                      'strokes to the cervical area of the '
                                      'tooth surface.',
                               'MC7': 'Covers the entire eara/surface of 

student_name student_id         assessor_name        date cohort  \
0      Jonathan Gershon    1391589     Melinda Johansson  2025-12-17   DDS2   
1  Sheng Weng Selwyn Lo    1432714           Jessica Tam  2025-05-29   DDS2   
2            Bella Dong    1154726          Rawan Hassan  2025-05-29   DDS2   
3    Michelle Onyekweli    1391595  Vinitha Soosaipillai  2025-05-29   DDS2   
4            Matthew Xu    1268586         Sowmya Sastry  2025-05-29   DDS2   

     subject        type student_role       clinic_type  patient_age  \
0  DENT90146  Simulation                             GP            0   
1  DENT90146      Clinic     Operator  General Practice            0   
2  DENT90146      Clinic     Operator  General Practice           51   
3  DENT90146      Clinic     Operator  General Practice           61   
4  DENT90146      Clinic     Operator  General Practice            0   

  patient_drn                     patient_status teeth_quadrant_info  \
0                                                                      
1                         Failed to attend (FTA)          Full mouth   
2     6231053                    I saw a patient         whole mouth   
3      814135                    I saw a patient    Entire dentition   
4              Patient cancelled within 24 hours                       

   student_submitted  assessor_submitted student_524_MC1 student_524_MC2  \
0               True                True             Yes             Yes   
1               True               False                                   
2              False                True                                   
3              False               False                                   
4               True               False                                   

  student_524_MC3 student_524_MC4 student_524_MC5 student_524_MC6  \
0    Not Assessed    Not Assessed    Not Assessed    Not Assessed   
1                                                                   
2                                                                   
3                                                                   
4                                                                   

  student_524_MC7 student_524_MC8 student_524_MC9 student_578_MC1  \
0             Yes              No              No             Yes   
1                                                                   
2                                                                   
3                                                                   
4                                                                   

  student_578_MC2 student_578_MC3 student_578_MC4 student_578_MC5  \
0              No              No              No              No   
1                                                                   
2                                                                   
3                                                                   
4                                                                   

  student_524_MC10 student_524_MC11 student_524_MC12 student_524_MC13  \
0               No              Yes              Yes     Not Assessed   
1                                                                       
2                                                                       
3                                                                       
4                                                                       

  student_524_MC14 student_524_MC15 student_524_MC16 student_524_MC17  \
0              Yes              Yes              Yes              Yes   
1                                                                       
2                                                                       
3                                                                       
4                                                                       

                                    student_feedback time_mgmt entrustment  \
0  Time mana

In [26]:
def createStudentReport(df, studentID):
    elements = []
    studentdf = df[df['student_id'] == studentID]
    studentName = studentdf['student_name'].iloc[0]
    # sort by date
    studentdf['date'] = pd.to_datetime(studentdf['date']).dt.date
    studentdf.sort_values('date', inplace=True)
    studentdf['date'] = studentdf['date']
    # filter out 31 march 2025 and 7 april 2025
    # studentdf = studentdf[studentdf['date'].isin(['31-03-2025', '07-04-2025'])]
    savefolder = f'{folder}\\Student Reports'#\\31Mar-7Apr'
    os.makedirs(savefolder, exist_ok=True)
    doc = SimpleDocTemplate(f'{savefolder}\\{studentID} ({studentName}).pdf', pagesize= pageSize, leftMargin = leftMargin,
                            rightMargin = rightMargin, topMargin = topMargin, bottomMargin = bottomMargin)
    
    # first heading
    elements.append(Paragraph(f'{studentName}', headingStyle))
    elements.append(Spacer(1, 24))

    # get the forms
    for i, (idx, row) in enumerate(studentdf.iterrows()):
        formitems = row['Items']
        type = row['type']
        elements.append(Paragraph(f'Form {i+1}: {row[colDate.lower()]}', subheadingStyle))
        elements.append(Spacer(1, 12))
        # elements.append(Paragraph(f'Role: {row[colRole]}', subsubheadingStyle))
        if len(formitems) > 0:
            elements.append(Spacer(1, 12))
            elements.append(Paragraph('Items Performed', subsubheadingStyleL))
            elements.append(Spacer(1, 12))
            elements.append(Paragraph(', '.join(formitems), tableTextStyleL))
        elements.append(Spacer(1, 12))
        # add other columns
        for col in otherCols:
            if pd.isna(row[col]) or row[col] == 'nan' or row[col] == '':
                continue
            # print(f'{col}: {row[col]}')
            elements.append(Paragraph(f'{otherfullnamedict[col] if col in otherfullnamedict.keys() else col}', smallsubsubheadingStyleL))
            elements.append(Spacer(1, 6))
            # text = row[col]
            # print(col, row[col])
            # if type is not string, convert to string
            if not isinstance(row[col], str):
                row[col] = str(row[col])
            text = row[col].strip().replace('\n', '<br/>')
            # remove _x000D_
            text = re.sub(r'_x000D_', '', text)
            # remove non-ascii characters
            text = re.sub(r'[^\x00-\x7F]+', '', text)
            elements.append(Paragraph(f'{text}', tableTextStyleL))
            elements.append(Spacer(1, 12))


        rubricDf = pd.DataFrame(columns = ['Rubric', 'Score'])
        for col in rubricCols:
            if pd.isna(row[col]) or row[col] == 'nan' or row[col] == '':
                continue
            rubricDf = pd.concat([rubricDf, pd.DataFrame({'Rubric': [otherfullnamedict[col]], 'Score': [row[col]]})])
        if len(rubricDf) != 0:
            rubricTable = createTable(rubricDf, 'Rubric Scores', colRatio=[1, 3], customTextCols=[0, 1], tableTextStyle=tableTextStyleSmall)
            # alter top and bottom padding
            table = rubricTable._content[2]
            table.setStyle(TableStyle([
                ('TOPPADDING', (0, 0), (-1, -1), 7),
                ('BOTTOMPADDING', (0, 0), (-1, -1), 7),
            ]))
            elements.append(rubricTable)
            elements.append(Spacer(1, 12))
        # add mc col table
        for item in formitems:
            print('\n', item, type)
            stumcCol = [col for col in studentmcCols if item in col]
            assmcCol = [col for col in assessormcCols if item in col]
            print(f'Student MC Columns: {stumcCol}')
            print(f'Assessor MC Columns: {assmcCol}')
            if type == 'Simulation':
                if item not in simChecklist:
                    checklist = {'name': item, 'fields': {}}
                    print(f'Item {item} not found in simulation checklist')
                else:
                    print(f'Item {item} found in simulation checklist')
                    checklist = simChecklist[item]
                itemName = checklist['name']
            else:
                if item not in clinicChecklist:
                    checklist = {'name': item, 'fields': {}}
                else:
                    checklist = clinicChecklist[item]
                itemName = checklist['name']
            if len(studentmcCols) == 0 or len(assessormcCols) == 0:
                continue
            evaldf = pd.DataFrame(columns = ['Marking Checklist', 'Student', 'Educator'])
            for stucol, educol in zip(stumcCol, assmcCol):
                qno = stucol.split('_')[-1]
                if qno not in checklist['fields'].keys():
                    markingchecklist = qno
                    print(f'Question {qno} not found in checklist for item {item}')
                else:
                    markingchecklist = checklist['fields'][qno]
                student = row[stucol]
                educator = row[educol]
                # if both student and educator are empty, skip
                if (pd.isna(student) or student == '') and (pd.isna(educator) or educator == ''):
                    continue
                evaldf = pd.concat([evaldf, pd.DataFrame({'Marking Checklist': [markingchecklist], 'Student': [student], 'Educator': [educator]})])
            
            evaldf.replace({'Not Assessed': 'NA', 'Not Reviewed': 'NA', 'nan': 'NA'}, inplace=True)
            evalTable = createTable(evaldf, f'Evaluation for {item}: {itemName}', colRatio = [5, 1, 1], customTextCols=[0], cellHighlight=True, tableTextStyle=tableTextStyleSmall)
            # alter top and bottom padding
            table = evalTable._content[2]
            # if it's a table
            if isinstance(table, Table):
                table.setStyle(TableStyle([
                    ('TOPPADDING', (0, 0), (-1, -1), 7),
                    ('BOTTOMPADDING', (0, 0), (-1, -1), 7),
                ]))
            elements.append(evalTable)
            elements.append(Spacer(1, 12))
        # add pec table
        # pecdf = pd.DataFrame(columns = ['Marking Checklist', 'Student', 'Educator'])
        # for col in pecCols:
        #     pecdf = pd.concat([pecdf, pd.DataFrame({'Marking Checklist': [fullnamedict[col].split(' - ')[-1]], 'Student': [row[col]], 'Educator': [row[col.replace('#1', '#2')]]})])
        # pecdf.replace({'Not Assessed': 'NA', 'Not Reviewed': 'NA', 'nan': 'NA'}, inplace=True)
        # pecTable = createTable(pecdf, 'Other Marking Checklist', colRatio = [5, 1, 1], customTextCols=[0], cellHighlight=True, tableTextStyle=tableTextStyleSmall)
        # elements.append(pecTable)
        # table = pecTable._content[2]
        # table.setStyle(TableStyle([
        #     ('TOPPADDING', (0, 0), (-1, -1), 7),
        #     ('BOTTOMPADDING', (0, 0), (-1, -1), 7),
        # ]))
        elements.append(PageBreak())
    doc.build(elements)

for studentID in df['student_id'].unique():
    # print(studentID)
    # if int(studentID)!= 1538387:
        # continue
    createStudentReport(df, studentID)
    # break

Creating table for Rubric Scores

 577 Simulation
Student MC Columns: ['student_577_MC1', 'student_577_MC2', 'student_577_MC3', 'student_577_MC4', 'student_577-2_MC1', 'student_577-2_MC2', 'student_577-2_MC3', 'student_577-2_MC4']
Assessor MC Columns: ['assessor_577_MC1', 'assessor_577_MC2', 'assessor_577_MC3', 'assessor_577_MC4', 'assessor_577-2_MC1', 'assessor_577-2_MC2', 'assessor_577-2_MC3', 'assessor_577-2_MC4']
Item 577 found in simulation checklist
Creating table for Evaluation for 577: Cusp Capping per Cusp

 533 Simulation
Student MC Columns: ['student_533_MC1', 'student_533_MC2', 'student_533_MC3', 'student_533_MC4', 'student_533_MC5', 'student_533_MC6', 'student_533_MC7', 'student_533_MC8', 'student_533_MC9', 'student_533_MC10', 'student_533_MC11', 'student_533_MC12', 'student_533_MC13', 'student_533_MC14', 'student_533_MC15', 'student_533_MC16', 'student_533_MC17']
Assessor MC Columns: ['assessor_533_MC1', 'assessor_533_MC2', 'assessor_533_MC3', 'assessor_533_MC4', 'assesso

In [ ]:
plt.ioff()
colorDict = {
    'Yes': '#4c72b0',             # Muted Blue
    'Yes with guidance': '#55a868',  # Soft Green
    'No': '#e07a5f',             # Warm Red-Orange
    'Not assessed': '#bfbfbf',    # Neutral Grey
    'NA': '#bfbfbf'              # Grey for renamed 'Not assessed'
}

def getYesNo(df, stuCols, supCols):
    df['YesStu'] = df[stuCols].apply(lambda x: (x == 'Yes').sum(), axis=1)
    df['NoStu'] = df[stuCols].apply(lambda x: (x == 'No').sum(), axis=1)
    df['NAStu'] = df[stuCols].apply(lambda x: (x == 'NA').sum(), axis=1)
    df['ScoreStu'] = df['YesStu']/(df['YesStu'] + df['NoStu'] + 0.00001)
    df['YesSup'] = df[supCols].apply(lambda x: (x == 'Yes').sum(), axis=1)
    df['NoSup'] = df[supCols].apply(lambda x: (x == 'No').sum(), axis=1)
    df['NASup'] = df[supCols].apply(lambda x: (x == 'NA').sum(), axis=1)
    df['ScoreSup'] = df['YesSup']/(df['YesSup'] + df['NoSup'] + 0.00001)
    df['ScoreDiff'] = df['ScoreStu'] - df['ScoreSup']
    return df
colId = 'student_name'

def plotStackedYesNo(df, colId, title):
    plotdf = df[[colId, 'YesStu', 'NoStu', 'NAStu', 'YesSup', 'NoSup', 'NASup']]
    # sort by highest NoSup
    # display(plotdf)
    plotdf = plotdf.groupby(colId).sum()
    plotdf.sort_values(by='NoSup', ascending=True, inplace=True)
    # drop rows with YesStu and YesSup = 0 and NoStu and NoSup = 0
    plotdf = plotdf[(plotdf['YesStu'] + plotdf['YesSup'] > 0) & (plotdf['NoStu'] + plotdf['NoSup'] > 0)]
    if len(plotdf) < 5:
        return None
    # display(plotdf)
    # plotdf.set_index(colId, inplace=True)
    studf = plotdf[['YesStu', 'NoStu', 'NAStu']]
    studf.columns = ['Yes', 'No', 'NA']
    supdf = plotdf[['YesSup', 'NoSup', 'NASup']]
    supdf.columns = ['Yes', 'No', 'NA']
    colors = [colorDict[key] for key in ['Yes', 'No', 'NA']]
    fig, ax = plt.subplots(1, 2, figsize=(figSize[0], figSize[1]))
    studf.plot(kind='barh', stacked=True, ax=ax[0], color=colors)
    ax[0].set_title('Student')
    ax[0].set_yticklabels(ax[0].get_yticklabels(), fontsize=6)
    ax[0].set_ylabel('')
    supdf.plot(kind='barh', stacked=True, ax=ax[1], color=colors)
    ax[1].set_title('Supervisor')
    ax[1].set_ylabel('')    
    ax[1].set_yticklabels(ax[1].get_yticklabels(), fontsize=6)
    # hide legend for first plot
    ax[0].get_legend().remove()
    ax[1].legend(title='Evaluation', bbox_to_anchor=(1.05, 1.02))
    # add horizontal space
    plt.tight_layout()
    ax
    # fig.suptitle(title, y = 1.02)
    img = addPlotImage(fig, 0.9)
    return img

uniquevals = [ 'Yes','No', 'NA']
# colors = {'Yes': 'blue', 'No': 'orange', 'Not assessed': 'lightgrey', 'Not relevant': 'green'}
colors = ['blue', 'orange', 'lightgrey']
def figToImage(fig):
    """Converts a Matplotlib figure to a PIL Image"""
    buf = BytesIO()
    fig.savefig(buf, format='png', bbox_inches='tight')
    buf.seek(0)
    return PIL.Image.open(buf)

def getEvalCounts(df, colGeneralEval, checklist, item):
    # create df for evaluation counts for each column
    evalcountDf = pd.DataFrame(columns = ['Question'] + uniquevals)
    for col in colGeneralEval:
        evalcount = df[col].value_counts()
        # remove ''
        evalcount = evalcount.drop('', errors='ignore')
        if len(evalcount) ==0:
            return None
        print(evalcount)
        qno = col.split('_')[-1]
        if qno in checklist[item]['fields']:
            fulltext = checklist[item]['fields'][qno]
        else:
            fulltext = 'Not Found'
        evalcountDf = pd.concat([evalcountDf, pd.DataFrame({'Question': [qno],
                                                             **evalcount.to_dict()})])
    evalcountDf.fillna(0, inplace=True)
    # sort by the total sum of the columns
    evalcountDf['sum'] = evalcountDf[uniquevals].sum(axis=1)
    evalcountDf = evalcountDf.sort_values('sum', ascending=False)
    # remove rows with sum = 0
    evalcountDf = evalcountDf[evalcountDf['sum'] != 0]
    evalcountDf.drop('sum', axis=1, inplace=True)
    # sort by question where question is MC\d+ use the digit
    evalcountDf['Question Num'] = evalcountDf['Question'].str.extract(r'(\d+)', expand=False).astype(int)
    evalcountDf = evalcountDf.sort_values('Question Num')
    evalcountDf.drop('Question Num', axis=1, inplace=True)
    # if max value is less than 2 then return None
    if evalcountDf[uniquevals].max().max() < 2:
        return None
    # evalcountDf = evalcountDf.head(15)
    return evalcountDf

# create stacked bar chart for general evaluation counts
def createStackedBarChart(df, title, plotCol):
    fig, ax = plt.subplots(figsize=(figSize[0]*0.6, figSize[1]*0.8))
    plotdf = df.set_index(plotCol)
    plotdf = plotdf.loc[::-1]  # Reverse the order of bars
    if len(plotdf) == 0:
        return None
    # remove rows with all zeros
    plotdf = plotdf.loc[(plotdf!=0).any(axis=1)]
    
    plotdf.plot(kind='barh', stacked=True, ax=ax, color=colors)
    ax.set_title(title)
    ax.set_xlabel('Questions')
    ax.set_ylabel('Counts')
    ax.set_xticklabels(ax.get_xticklabels(), rotation=0, fontsize=8)
    ax.legend(loc='center left', bbox_to_anchor=(0.5, 1.1))
    plt.tight_layout()
    return fig


In [ ]:
# overall report
df.replace({'nan': 'NA', 'Not Assessed': "NA", "Not Reviewed": "NA"}, inplace=True)
elements = []

elements.append(Paragraph(f'Overall Report', headingStyle))
elements.append(Spacer(1, 24))
def getFrontTable(df):
    nforms = len(df)
    typecounts = df['type'].value_counts()
    entrustmentcounts = df['entrustment'].value_counts().drop('', errors='ignore')
    entrustmentcounts = entrustmentcounts.sort_index()
    # item counts
    allitems = []
    for idx, row in df.iterrows():
        allitems.extend(row['Items'])
    counts = pd.Series(allitems).value_counts()
    itemcounts = counts.to_dict()

    # create a table for the counts
    countdf = pd.DataFrame(columns = ['Metric', 'Value'])
    countdf = pd.concat([countdf, pd.DataFrame({'Metric': ['Number of Forms'], 'Value': [nforms]})])
    typecountText = '<br/> '.join([f'{key}: {value}' for key, value in typecounts.items()])
    # countdf = pd.concat([countdf, pd.DataFrame({'Metric': ['Type Counts'], 'Value': [typecountText]})])
    entrustmentText = '<br/> '.join([f'{int(key)}: {value}' for key, value in entrustmentcounts.items()])
    itemcountText = '<br/> '.join([f'{key}: {value}' for key, value in itemcounts.items()])
    countdf = pd.concat([countdf, pd.DataFrame({'Metric': ['Entrustment Counts'], 'Value': [entrustmentText]})])
    countdf = pd.concat([countdf, pd.DataFrame({'Metric': ['Item Counts'], 'Value': [itemcountText]})])
    countTable = createTable(countdf, 'Summary Table', colRatio=[3, 1], customTextCols=[0, 1], tableTextStyle=tableTextStyleLarge)
    return countTable

# create a student name and items table
studentItemDf = df[[colId, 'Items']]
#aggregate items with combining the item lists
studentItemDf = studentItemDf.groupby(colId).agg({'Items': 'sum'}).reset_index()

studentItemDf['Items'] = studentItemDf['Items'].apply(lambda x: list(set(x)))
studentItemDf['Items'] = studentItemDf['Items'].apply(lambda x: ', '.join(x))
studentItemDf = studentItemDf.sort_values(colId)
# studentItemTable = createTable(studentItemDf, 'Student Items Table', colRatio=[2, 2], customTextCols=[0, 1], tableTextStyle=tableTextStyleLarge)
# elements.append(studentItemTable)
# elements.append(Spacer(1, 128))
# elements.append(PageBreak())

# get all the items
validType = 'Clinic' # 'Simulation' or 'Clinic'
for type_ in df['type'].unique():
    print(type_)
    if validType is not None and type_ != validType:
        continue
    thisdf = df[df['type'] == type_]
    fronttable = getFrontTable(thisdf)
    elements.append(fronttable)
    elements.append(PageBreak())
    allitems = []
    for idx, row in thisdf.iterrows():
        allitems.extend(row['Items'])
    allitems = list(set(allitems))
    elements.append(Paragraph(f'{type_}', subheadingStyle))
    elements.append(Spacer(1, 12))
    checklist = simChecklist if type_ == 'Simulation' else clinicChecklist
    # create stackec bar chart of value counts for each column for ech item
    for item in allitems:
        if item not in checklist:
            continue
        print(item, checklist[item]['name'])

        stuCols = [col for col in studentmcCols if item in col]
        supCols = [col for col in assessormcCols if item in col]

        itemdf = getYesNo(thisdf, stuCols, supCols)
        imgstuEval = plotStackedYesNo(itemdf, colId, item)
        
        
        evalcountDfStu = getEvalCounts(thisdf, stuCols, checklist, item)
        evalcountDfSup = getEvalCounts(thisdf, supCols, checklist, item)
        if evalcountDfStu is None or evalcountDfSup is None:
            continue
        # display(evalcountDf.head())
        figStu = createStackedBarChart(evalcountDfStu, 'Student', 'Question')
        figSup = createStackedBarChart(evalcountDfSup, 'Supervisor', 'Question')
        if figStu is None or figSup is None:
            continue
        imgSup = figToImage(figSup)
        imgStu = figToImage(figStu)
        fig, axes = plt.subplots(1, 2, figsize=(figSize[0], figSize[1]))
        axes[0].imshow(imgStu)
        axes[0].axis('off')
        axes[1].imshow(imgSup)
        axes[1].axis('off')
        plt.tight_layout()
        
        img = addPlotImage(fig, 0.85)
        # elements.append(Paragraph(f'{item}: {checklist[item]["name"]}', subsubheadingStyle))
        # elements.append(Spacer(1, 12))
        if imgstuEval is not None:
            elements.append(Paragraph(f'{item}: {checklist[item]["name"]}', subsubheadingStyle))
            elements.append(Spacer(1, 12))
            elements.append(imgstuEval)
            elements.append(PageBreak())
        # elements.append(Spacer(1, 24))
        elements.append(Paragraph('Question wise evaluation', subsubheadingStyle))
        elements.append(img)
        # create a full text reference table
        fulltextdf = pd.DataFrame(columns = ['Question', 'Full Text'])
        for qno, text in checklist[item]['fields'].items():
            fulltextdf = pd.concat([fulltextdf, pd.DataFrame({'Question': [qno], 'Full Text': [text]})])
        fulltextdf['Question Num'] = fulltextdf['Question'].str.extract(r'(\d+)', expand=False).astype(int)
        fulltextdf = fulltextdf.sort_values('Question Num')
        fulltextdf.drop('Question Num', axis=1, inplace=True)
        toppadding = 6
        bottompadding = 6
        if len(fulltextdf) > 10:
            toppadding = 3
            bottompadding = 3
        fulltextTable = createTable(fulltextdf, 'MC Reference Table', colRatio=[1, 3], customTextCols=[0, 1], tableTextStyle=tableTextStyleSmall,
                                    tableWidth=0.9, topPadding=toppadding, bottomPadding=bottompadding)
        elements.append(fulltextTable)
        elements.append(PageBreak())

doc = SimpleDocTemplate(f'{folder}\\Overall Report Student Eval {validType}.pdf', pagesize= pageSize, leftMargin = leftMargin,
                        rightMargin = rightMargin, topMargin = topMargin, bottomMargin = bottomMargin)
doc.build(elements)